# NOTES
- make relTime and objTime also sequencing?

In [1]:
import json
import random
import balance
#import visualize
import seaborn as sns
import pandas as pd
import matplotlib.pyplot as plt
import pickle
import grammar as g

In [2]:

with open('../exports/dataset/to_direct.txt', 'rb') as f:
    to_direct = json.load(f)

with open('../data/templ2global.txt', 'rb') as f:
    templ2global = json.load(f)

def translateType(tp):
    if tp == 'query':
        return 'open'
    else:
        return 'binary'
    

In [3]:
def getVideoIDS(group):
    if group == 'train':
        return list(train_stsgs)
    elif group == 'test':
        return list(test_stsgs)
    
def loadJSON(path):
    with open(path) as json_file:
        QA = json.load(json_file)
    return QA

def getQA(d_path, group, bal_txt, v_id):
    with open('../exports/%s/%s/%s/%s.txt' % (d_path, bal_txt, group, v_id)) as json_file: #CHANGED
        QA = json.load(json_file)
    return QA

def getSTSGS(group):
    if group == 'train':
        return train_stsgs
    elif group == 'test':
        return test_stsgs
    else:
        print("INVALID GROUP", group)
        return
        

In [4]:
infile = open('../data/stsgs/train_stsgs.pkl', 'rb')
train_stsgs = pickle.load(infile)
infile.close()

infile = open('../data/stsgs/test_stsgs.pkl', 'rb')
test_stsgs = pickle.load(infile)
infile.close()


In [5]:
def pickleDump(var, destination):
    f = open(destination,"wb")
    pickle.dump(var,f)
    f.close() 
    
    
def pickleLoad(path):
    file = open(path, 'rb')
    info = pickle.load(file)
    file.close()
    return info


In [6]:
def getDF(qs):
    for q in qs:
        for i in q['attributes']:
            q[i] = q['attributes'][i]
            
    return pd.DataFrame(qs)

#df = getDF(test_qs)

In [26]:
# Testing to CSV
#46GP8, N11GT, KRF68, MJO7C, S6MPZ

def mark(x):
    if x:
        return 1
    return 0

# INDIRECTS is [obj, rel, action, time]
def toDataframe(v_id, QA, explode_global=False):
    for q_id in QA:
        q = QA[q_id]
        for i in q['attributes']:
            q[i] = q['attributes'][i]
            
        q['global'] = templ2global[q['attributes']['type']]
        q['ans_type'] = translateType(q['attributes']['structural'])
        if q['semantic'] == 'objrel':
            q['semantic'] = 'relation'
    
            
        
        for i in q['metrics']:
            q[i] = q['metrics'][i]
            
        nc = q['novel_comp']
        q['novel_comp'] = mark(nc.count(True) != 0)
        q['nc_seq'] = mark(nc[0])
        q['nc_sup'] = mark(nc[1])
        q['nc_dur'] = mark(nc[2])
        q['nc_objrel'] = mark(nc[4])
        
        indir = q['indirects']
        q['indirect'] = mark(indir.count(True) != 0)
        q['i_obj'] = mark(indir[0])
        q['i_rel'] = mark(indir[1])
        q['i_act'] = mark(indir[2])
        q['i_temp'] = mark(indir[3])
        
        if q_id not in to_direct:
            q['direct_equiv'] = None
        else:
            q['direct_equiv'] = to_direct[q_id]
        
    df = pd.DataFrame.from_dict(QA, orient="index")
    df['vid_id'] = v_id
    
    if explode_global:
        df = splitDataFrameList(df, 'global')
        
    return df



def toCSVBal(d_path, group, bal_txt, explode_global=False):
    dataframes = []
    if group == 'train':
        our_data = train_stsgs
    if group == 'test':
        our_data = test_stsgs
        
    cnt = 0
    for v_id in our_data:
        if cnt % 100 == 0:
            print(cnt)
        cnt = cnt + 1
        QA = getQA(d_path, group, bal_txt, v_id)
        df = toDataframe(v_id, QA, explode_global)
        dataframes.append(df)
    total = pd.concat(dataframes)
    if explode_global:
        path = '../exports/%s/other_formats/%s-%s-agqa-global.csv' % (d_path, group, bal_txt)
        
    else:
        path = '../exports/%s/other_formats/%s-%s-agqa.csv' % (d_path, group, bal_txt)
    print('saving to: ', path)
    total.to_csv(path, index = None)
    return total


In [27]:
def splitDataFrameList(df,target_column,separator=None):
    ''' df = dataframe to split,
    target_column = the column containing the values to split
    separator = the symbol used to perform the split
    returns: a dataframe with each entry for the target column separated, with each element moved into a new row. 
    The values in the other columns are duplicated across the newly divided rows.
    '''
    def splitListToRows(row,row_accumulator,target_column,separator):
        split_row = row[target_column]#.split(separator)
        for s in split_row:
            new_row = row.to_dict()
            new_row[target_column] = s
            row_accumulator.append(new_row)
    new_rows = []
    df.apply(splitListToRows,axis=1,args = (new_rows,target_column,separator))
    new_df = pd.DataFrame(new_rows)
    return new_df

In [28]:
test_csv = toCSVBal('dataset', 'test', 'balanced', explode_global=False)

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
saving to:  ../exports/dataset/other_formats/test-balanced-agqa.csv


In [31]:
test_csv_g = toCSVBal('dataset', 'test', 'balanced', explode_global=True)

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
saving to:  ../exports/dataset/other_formats/test-balanced-agqa-global.csv


In [29]:
train_csv = toCSVBal('dataset', 'train', 'balanced', explode_global=False)

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
saving to:  ../exports/dataset/other_formats/train-balanced-agqa.csv


In [30]:
train_csv_g = toCSVBal('dataset', 'train', 'balanced', explode_global=True)

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
saving to:  ../exports/dataset/other_formats/train-balanced-agqa-global.csv


# Camera metrics

In [14]:
path = '../exports/%s/other_formats/%s-%s-agqa.csv'
path_g = '../exports/%s/other_formats/%s-%s-agqa-global.csv'

#train_qs = pd.read_csv(path % ('dataset', 'train', 'balanced'))
df_qs = pd.read_csv(path % ('dataset', 'test', 'balanced'))

#train_qs_g = pd.read_csv(path_g % ('dataset', 'train', 'balanced'))
df_qs_g = pd.read_csv(path_g % ('dataset', 'test', 'balanced'))


In [15]:

with open('../data/template_ids.txt') as json_file:
    templ_ids_dict = json.load(json_file)
    
templ_ids = []

for i in templ_ids_dict:
    templ_ids.append(i)


In [16]:

bny = {
    'objExists': 0,
    'objRelExists': 0,
    'relExists': 0,
    'actExists': 0,
    'andObjRelExists': 0,
    'xorObjRelExists': 0,
    'objFirstVerify': 0,
    'objLastVerify': 0,
    'actTime': 0,
    'relTime': 0,
    'objTime': 0,
    'actLengthLongerVerify': 0,
    'actLengthShorterVerify': 0,
    #'actCountChooseMore': 0,
    #'actCountChooseFewer': 0,
    #'actLengthLongerChoose': 0,
    'actLengthShorterChoose': 0,
    'objFirstChoose': 0,
    'objLastChoose': 0,
    'objWhatChoose': 0,
}
    
opn = {
    'objWhat': 0,
    'objWhatGeneral': 0,
    'objFirst': 0,
    #'relFirst': 0,
    'objLast': 0,
    #'relLast': 0,
    #'actCount': 0,
    'actWhatAfterAll': 0,
     'actWhatBefore': 0,
     'actLast': 0,
     'actFirst': 0,
     'actLongest': 0,
     'actShortest': 0,
}

In [17]:
def getQA(d_path, v_id, group, getall=False):
    if getall: 
        bal_text = 'all'
    else:
        bal_text = 'balanced'
    with open('../exports/%s/%s/%s/%s.txt' % (d_path, bal_text, group, v_id)) as json_file:
        QA = json.load(json_file)
    return QA
    
def getSTSGS(group):
    if group == 'train':
        return train_stsgs
    elif group == 'test':
        return test_stsgs
    else:
        print("INVALID GROUP", group)
        return
    
def sums(dic):
    s = 0
    for i in dic:
        s = s + dic[i]
    return s

def total(dic):
    tot = 0
    for i in dic:
        tot = tot + dic[i]
    return tot

def perc(num, denom):
    if denom == 0:
        return 'denom 0'
    return round(num / denom  * 100, 2)
        

In [18]:
def findMax(ans):
    #print("finding max for ", ans)
    mx = 0
    tot = 0
    
    for a in ans:
        cnt = ans[a]
        tot = tot + cnt
        if cnt > mx:
            mx = cnt
            #print("Current Max: ", mx)
                
    return mx, tot

def randomChanceByTempl(by_templ):
    
    rand = {}
    for t in by_templ:
        mx, tot = findMax(by_templ[t])
        if tot == 0:
            #print("tot is 0 for template ", t)
            perc = 0
        else:
            perc = round(mx / tot, 3)
            
        rand[t] = (perc, mx, tot)
        
    return rand
        

In [19]:
def true(x):
    if x:
        return 1
    return 0

def combineSemantic(x):
    if x == 'objrel':
        return 'relation'
    else:
        return x

# Evaluate preds

In [20]:
def getPredsList(d_path, model, metric, group):
    path = preds_path 
    print("getting preds from: ", path)
    with open(path) as f:
        preds = json.load(f)
    
    return preds

def getPredsDic(preds_list):
    preds_dic = {}
    preds_dic['Total_preds'] = {i['csv_q_id']: 1 for i in preds_list}
    for descr in preds_list[0]:
        if descr == 'question': 
            descr2 = 'words'
        elif descr == 'answer':
            descr2 = 'AGQA_ans'
        else:
            descr2 = descr
        preds_dic[descr2] = {i['csv_q_id']: i[descr] for i in preds_list}
    
    if 'id' in preds_dic:
        preds_dic.pop('id')

    return preds_dic


def makePredsDF(d_path, model, metric, group, exploded_global=False):
    preds_list = getPredsList(d_path, model, metric, group)
    
    if exploded_global:
        df = df_qs_g
    else:
        df = df_qs
    dics = []
    
    start = 0
    split = 50000
    preds_dic = getPredsDic(preds_list)
    
    for i in preds_dic:
        df[i] = df['id'].map(preds_dic[i])

    df = df[df['Total_preds'] == 1]
    
    
    df.loc[:,'semantic'] = df['semantic'].apply(combineSemantic)
    df.loc[:,'correct'] = df['AGQA_ans'] == df['prediction']
    df.loc[:,'correct'] = df['correct'].apply(true)
    return df

In [35]:
d_path = 'dataset'
model = 'hcrn'
metric = 'balanced'
group = 'test'

In [38]:
#with open('../testing_blind/test_preds_blind3.json', 'rb') as f:
#    preds = json.load(f)

preds_path = '../exports/dataset/results/hcrn/%s/preds/preds_%s_3.json' % (metric, metric)

In [39]:

#preds_glob = makePredsDF(d_path, model, metric, group, exploded_global=True)
preds = makePredsDF(d_path, model, metric, group, exploded_global=False)

getting preds from:  ../exports/dataset/results/hcrn/balanced/preds/preds_balanced_3.json


In [40]:
preds.shape

(606407, 36)

In [68]:
print(preds.groupby(['semantic', 'ans_type']).mean().correct.to_dict())

{('action', 'binary'): 0.5130721883590296, ('action', 'open'): 0.04787592717464599, ('object', 'binary'): 0.40523539241275497, ('object', 'open'): 0.30467339028795226, ('relation', 'binary'): 0.5204939892504}


In [69]:
preds.groupby(['semantic', 'ans_type', 'correct']).sum().Total_preds.to_dict()


{('action', 'binary', 0): 32593,
 ('action', 'binary', 1): 34343,
 ('action', 'open', 0): 1412,
 ('action', 'open', 1): 71,
 ('object', 'binary', 0): 86135,
 ('object', 'binary', 1): 58687,
 ('object', 'open', 0): 205590,
 ('object', 'open', 1): 90084,
 ('relation', 'binary', 0): 46748,
 ('relation', 'binary', 1): 50744}

In [44]:
print(preds.groupby(['Total_preds']).mean().correct)
print()
print(preds.groupby(['Total_preds', 'ans_type']).mean().correct)
print()
print(preds.groupby(['semantic']).mean().correct)
print()
print(preds.groupby(['semantic', 'ans_type']).mean().correct)
print()
print(preds.groupby(['structural']).mean().correct)

Total_preds
1    0.385762
Name: correct, dtype: float64

Total_preds  ans_type
1            binary      0.464912
             open        0.303392
Name: correct, dtype: float64

semantic
action      0.502989
object      0.337735
relation    0.520494
Name: correct, dtype: float64

semantic  ans_type
action    binary      0.513072
          open        0.047876
object    binary      0.405235
          open        0.304673
relation  binary      0.520494
Name: correct, dtype: float64

structural
choose     0.351201
compare    0.528514
logic      0.503904
query      0.303392
verify     0.505406
Name: correct, dtype: float64


In [42]:
print(preds.groupby(['type']).mean().correct)

type
actExists                 0.499596
actFirst                  0.034111
actLast                   0.014286
actLengthLongerChoose     0.291283
actLengthLongerVerify     0.508594
actLengthShorterChoose    0.298956
actLengthShorterVerify    0.495089
actLongest                0.076677
actShortest               0.018868
actTime                   0.556446
actWhatAfterAll           0.058020
actWhatBefore             0.062992
andObjRelExists           0.508817
objExists                 0.511980
objFirst                  0.166294
objFirstChoose            0.340476
objFirstVerify            0.499451
objLast                   0.159976
objLastChoose             0.385702
objLastVerify             0.508691
objRelExists              0.505654
objTime                   0.656250
objWhat                   0.345547
objWhatChoose             0.329186
objWhatGeneral            0.099769
relExists                 0.507875
relTime                   0.544167
xorObjRelExists           0.498990
Name: correct, 

In [43]:

preds_g = makePredsDF(d_path, model, metric, group, exploded_global=True)

getting preds from:  ../exports/dataset/results/hcrn/balanced/preds/preds_balanced_3.json


In [34]:
print(preds_g.groupby(['global']).mean().correct)
print()
print(preds_g.groupby(['global', 'ans_type']).mean().correct)

global
action-recognition     0.043868
duration-comparison    0.419690
exists                 0.500179
obj-act                0.593750
obj-rel                0.360078
rel-act                0.532107
sequencing             0.544899
superlative            0.354543
Name: correct, dtype: float64

global               ans_type
action-recognition   open        0.043868
duration-comparison  binary      0.430556
                     open        0.032787
exists               binary      0.500179
obj-act              binary      0.593750
obj-rel              binary      0.477372
                     open        0.290250
rel-act              binary      0.532107
sequencing           binary      0.550351
                     open        0.038095
superlative          binary      0.486357
                     open        0.161480
Name: correct, dtype: float64


In [70]:
print(preds_g.groupby(['global']).mean().correct.to_dict())

{'action-recognition': 0.04118173679498657, 'duration-comparison': 0.3894611135990446, 'exists': 0.5054852604657424, 'obj-act': 0.65625, 'obj-rel': 0.3493729039764561, 'rel-act': 0.5441671045717289, 'sequencing': 0.5511579587493032, 'superlative': 0.31353259620540846}


In [71]:
preds_g.groupby(['global', 'correct']).sum().Total_preds.to_dict()


{('action-recognition', 0): 1071,
 ('action-recognition', 1): 46,
 ('duration-comparison', 0): 8180,
 ('duration-comparison', 1): 5218,
 ('exists', 0): 44085,
 ('exists', 1): 45063,
 ('obj-act', 0): 22,
 ('obj-act', 1): 42,
 ('obj-rel', 0): 304202,
 ('obj-rel', 1): 163350,
 ('rel-act', 0): 17349,
 ('rel-act', 1): 20711,
 ('sequencing', 0): 17714,
 ('sequencing', 1): 21752,
 ('superlative', 0): 107531,
 ('superlative', 1): 49113}

# To look at:

- Answer distribution of yes/no questions and before/after questions
- maybe it's lower because of 'choose' and 'compare' etc

### Exists

In [120]:
exists = preds_g[preds_g['global'] == 'exists']
exists.shape

(92032, 36)

In [121]:
exists['Total'] = 1
exists.columns


/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


Index(['question', 'answer', 'attributes', 'global', 'local', 'steps', 'id',
       'metrics', 'program', 'sg_grounding', 'type', 'structural', 'semantic',
       'ans_type', 'video_id', 'novel_comp', 'indirects', 'direct_args',
       'direct_time', 'nc_before', 'nc_first', 'nc_longer', 'nc_objrel',
       'indir_obj', 'indir_rel', 'indir_act', 'indir_time', 'vid_id',
       'Total_preds', 'question_id', 'video_name', 'csv_q_id', 'words',
       'AGQA_ans', 'prediction', 'correct', 'Total'],
      dtype='object')

In [123]:
#exists2 = exists[exists['answer'] == 'Yes']
exists.groupby(['prediction']).count()

question  answer  attributes  global  local  steps     id  \
prediction                                                              
Yes            92032   92032       92032   92032  92032  92032  92032   

            metrics  program  sg_grounding  ...  indir_time  vid_id  \
prediction                                  ...                       
Yes           92032    92032         92032  ...       92032   92032   

            Total_preds  question_id  video_name  csv_q_id  words  AGQA_ans  \
prediction                                                                    
Yes               92032        92032       92032     92032  92032     92032   

            correct  Total  
prediction                  
Yes           92032  92032  

[1 rows x 36 columns]

# Thoughts

1. why are there so many more 'yes' than 'no'??

In [124]:
#exists2 = exists[exists['answer'] == 'Yes']
exists.groupby(['prediction']).count()

question  answer  attributes  global  local  steps     id  \
prediction                                                              
Yes            92032   92032       92032   92032  92032  92032  92032   

            metrics  program  sg_grounding  ...  indir_time  vid_id  \
prediction                                  ...                       
Yes           92032    92032         92032  ...       92032   92032   

            Total_preds  question_id  video_name  csv_q_id  words  AGQA_ans  \
prediction                                                                    
Yes               92032        92032       92032     92032  92032     92032   

            correct  Total  
prediction                  
Yes           92032  92032  

[1 rows x 36 columns]

### Before/after

In [20]:
ba = preds[(preds['type'] == 'actTime')| (preds['type'] == 'relTime') | (preds['type'] == 'objTime')]
ba.shape

(79644, 36)

In [21]:
ba.columns

Index(['question', 'answer', 'attributes', 'global', 'local', 'steps', 'id',
       'metrics', 'program', 'sg_grounding', 'type', 'structural', 'semantic',
       'ans_type', 'video_id', 'novel_comp', 'indirects', 'direct_args',
       'direct_time', 'nc_before', 'nc_first', 'nc_longer', 'nc_objrel',
       'indir_obj', 'indir_rel', 'indir_act', 'indir_time', 'vid_id',
       'Total_preds', 'question_id', 'video_name', 'csv_q_id', 'words',
       'AGQA_ans', 'prediction', 'correct'],
      dtype='object')

In [22]:
ba.groupby(['prediction']).count()

question  answer  attributes  global  local  steps     id  \
prediction                                                              
after          67393   67393       67393   67393  67393  67393  67393   
before         12251   12251       12251   12251  12251  12251  12251   

            metrics  program  sg_grounding  ...  indir_act  indir_time  \
prediction                                  ...                          
after         67393    67393         67393  ...      67393       67393   
before        12251    12251         12251  ...      12251       12251   

            vid_id  Total_preds  question_id  video_name  csv_q_id  words  \
prediction                                                                  
after        67393        67393        67393       67393     67393  67393   
before       12251        12251        12251       12251     12251  12251   

            AGQA_ans  correct  
prediction                     
after          67393    67393  
before         12251    12251  

[2 rows x 35 columns]

In [23]:
ba.groupby(['type', 'direct_time', 'answer']).count()

question  attributes  global  local  steps     id  \
type    direct_time answer                                                      
actTime ['all', ''] after      20015       20015   20015  20015  20015  20015   
                    before     20015       20015   20015  20015  20015  20015   
objTime ['all', ''] after         32          32      32     32     32     32   
                    before        32          32      32     32     32     32   
relTime ['all', ''] after      19775       19775   19775  19775  19775  19775   
                    before     19775       19775   19775  19775  19775  19775   

                            metrics  program  sg_grounding  structural  ...  \
type    direct_time answer                                              ...   
actTime ['all', ''] after     20015    20015         20015       20015  ...   
                    before    20015    20015         20015       20015  ...   
objTime ['all', ''] after        32       32            32          32  ...   
                    before       32       32            32          32  ...   
relTime ['all', ''] after     19775    19775         19775       19775  ...   
                    before    19775    19775         19775       19775  ...   

                            indir_time  vid_id  Total_preds  question_id  \
type    direct_time answer                                                 
actTime ['all', ''] after        20015   20015        20015        20015   
                    before       20015   20015        20015        20015   
objTime ['all', ''] after           32      32           32           32   
                    before          32      32           32           32   
relTime ['all', ''] after        19775   19775        19775        19775   
                    before       19775   19775        19775        19775   

                            video_name  csv_q_id  words  AGQA_ans  prediction  \
type    direct_time answer                                                      
actTime ['all', ''] after        20015     20015  20015     20015       20015   
                    before       20015     20015  20015     20015       20015   
objTime ['all', ''] after           32        32     32        32          32   
                    before          32        32     32        32          32   
relTime ['all', ''] after        19775     19775  19775     19775       19775   
                    before       19775     19775  19775     19775       19775   

                            correct  
type    direct_time answer           
actTime ['all', ''] after     20015  
                    before    20015  
objTime ['all', ''] after        32  
                    before       32  
relTime ['all', ''] after     19775  
                    before    19775  

[6 rows x 33 columns]

In [25]:
args = ba.T.to_dict().values()

In [33]:
from collections import defaultdict

In [58]:
org = {}

for i in args:
    indir = i['indirects']
    
        
    t = i['type']
    a = i['direct_args']
    ans = i['answer']
    
    if t not in org:
        org[t] = {}
    if a not in org[t]:
        org[t][a] = {}
    if indir not in org[t][a]:
        org[t][a][indir] = {}
    if ans not in org[t][a][indir]:
        org[t][a][indir][ans] = {'answer': 0, 'correct': 0}
    org[t][a][indir][ans]['answer'] += 1
    if i['correct']:
        org[t][a][indir][ans]['correct'] += 1

In [66]:
for t in ['actTime']:#org:
    for ar in org[t]:
        for indir in org[t][ar]:
            lens_ans = set()
            lens_cor = set()
            answers = []
            for ans in org[t][ar][indir]:
                lens_ans.add(org[t][ar][indir][ans]['answer'])
                lens_cor.add(org[t][ar][indir][ans]['correct'])
                answers.append(ans)

            if True:#len(lens_ans) != 1:
                tot_ans = 0
                tot_cor = 0
                
                for i in lens_ans:
                    tot_ans += i
                for i in lens_cor:
                    tot_cor += i
                perc = tot_cor / tot_ans
                
                print(t, ar, indir)
                print(answers)
                print(perc, lens_ans, lens_cor)
                
            
# 

actTime c137-c151 [False, False, False, False]
['after', 'before']
1.0 {2} {0, 2}
actTime c151-c150 [False, False, False, False]
['before', 'after']
1.0 {2} {0, 2}
actTime c138-c150 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c059-c148 [False, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c059-c096 [False, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c059-c096 [True, False, False, False]
['after', 'before']
1.0 {4} {4}
actTime c148-c155 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c148-c059 [True, False, False, False]
['before', 'after']
0.8571428571428571 {3, 4} {2, 4}
actTime c148-c059 [False, False, False, False]
['before']
1.0 {1} {1}
actTime c096-c059 [True, False, False, False]
['before', 'after']
0.8 {2, 3} {1, 3}
actTime c096-c059 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c026-c065 [False, False, False, False]
['before', 'after']
0.25 {1, 3} {0, 1}
actTime c026-c065 [Tr

actTime c053-c135 [True, False, False, False]
['after', 'before']
1.6666666666666667 {3} {2, 3}
actTime c053-c000 [True, False, False, False]
['after', 'before']
0.2727272727272727 {5, 6} {3}
actTime c053-c000 [False, False, False, False]
['after', 'before']
0.6666666666666666 {1, 2} {0, 2}
actTime c134-c072 [True, False, False, False]
['after', 'before']
0.3333333333333333 {1, 2} {0, 1}
actTime c134-c072 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c134-c054 [True, False, False, False]
['before', 'after']
1.1666666666666667 {6} {1, 6}
actTime c134-c001 [True, False, False, False]
['before', 'after']
0.6153846153846154 {6, 7} {1, 7}
actTime c134-c001 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c134-c053 [True, False, False, False]
['before', 'after']
1.1428571428571428 {7} {1, 7}
actTime c134-c002 [True, False, False, False]
['before', 'after']
1.0 {7} {0, 7}
actTime c002-c135 [True, False, False, False]
['after', 'before']
1.2857142857142858 {7} {4, 5}
ac

1.0 {5} {0, 5}
actTime c008-c001 [True, False, False, False]
['before', 'after']
1.0 {6} {1, 5}
actTime c008-c001 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c097-c002 [True, False, False, False]
['before', 'after']
0.45454545454545453 {5, 6} {0, 5}
actTime c097-c002 [False, False, False, False]
['before', 'after']
0.6666666666666666 {1, 2} {0, 2}
actTime c000-c006 [True, False, False, False]
['after', 'before']
0.46153846153846156 {6, 7} {2, 4}
actTime c000-c006 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c000-c073 [True, False, False, False]
['after', 'before']
0.6923076923076923 {6, 7} {3, 6}
actTime c000-c073 [False, False, False, False]
['before']
1.0 {1} {1}
actTime c141-c070 [True, False, False, False]
['before', 'after']
0.5454545454545454 {5, 6} {0, 6}
actTime c141-c070 [False, False, False, False]
['before', 'after']
0.3333333333333333 {1, 2} {0, 1}
actTime c073-c002 [True, False, False, False]
['before', 'after']
0.8571428571428571

1.0 {2} {0, 2}
actTime c108-c063 [True, False, False, False]
['before', 'after']
1.0 {5} {0, 5}
actTime c030-c110 [False, False, False, False]
['before', 'after']
1.0 {3} {0, 3}
actTime c030-c043 [False, False, False, False]
['before', 'after']
0.3333333333333333 {1, 2} {0, 1}
actTime c030-c043 [True, False, False, False]
['after', 'before']
0.8 {2, 3} {1, 3}
actTime c115-c109 [False, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c115-c142 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c115-c142 [True, False, False, False]
['after', 'before']
0.3333333333333333 {1, 2} {1}
actTime c107-c110 [False, False, False, False]
['before', 'after']
1.0 {5} {0, 5}
actTime c107-c026 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c120-c109 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c120-c110 [False, False, False, False]
['before', 'after']
1.0 {4} {0, 4}
actTime c120-c043 [False, False, False, False]
['before']
0.0 {

1.0 {1} {1}
actTime c098-c015 [True, False, False, False]
['before']
1.0 {1} {1}
actTime c098-c017 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c098-c017 [True, False, False, False]
['before']
0.0 {1} {0}
actTime c039-c015 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c039-c015 [True, False, False, False]
['before']
1.0 {1} {1}
actTime c042-c017 [False, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c042-c017 [True, False, False, False]
['before', 'after']
1.0 {4} {0, 4}
actTime c098-c041 [True, False, False, False]
['after', 'before']
0.8461538461538461 {6, 7} {4, 7}
actTime c098-c041 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c100-c042 [True, False, False, False]
['before', 'after']
0.5 {2} {1}
actTime c041-c098 [True, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c015-c098 [True, False, False, False]
['before', 'after']
0.14285714285714285 {3, 4} {1}
actTime c015-c098 [False, False, False, False]
['after'

...

1.0 {6} {2, 4}
actTime c015-c021 [False, False, False, False]
['before', 'after']
0.0 {1} {0}
actTime c021-c071 [True, False, False, False]
['before', 'after']
0.6923076923076923 {6, 7} {2, 7}
actTime c021-c071 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c022-c015 [True, False, False, False]
['after', 'before']
0.2727272727272727 {5, 6} {3}
actTime c022-c015 [False, False, False, False]
['after']
0.0 {1} {0}
actTime c022-c016 [True, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c071-c021 [True, False, False, False]
['after', 'before']
1.25 {4} {2, 3}
actTime c071-c024 [True, False, False, False]
['after', 'before']
1.0 {4} {0, 4}
actTime c134-c016 [True, False, False, False]
['after', 'before']
1.0 {1} {1}
actTime c024-c071 [True, False, False, False]
['before', 'after']
0.7142857142857143 {3, 4} {2, 3}
actTime c024-c071 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c024-c070 [True, False, False, False]
['before', 'after']
0.58333333333333

actTime c040-c015 [True, False, False, False]
['after', 'before']
1.0 {6} {6}
actTime c040-c016 [False, False, False, False]
['after']
1.0 {2} {2}
actTime c040-c016 [True, False, False, False]
['before']
1.0 {2} {2}
actTime c042-c015 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c042-c015 [True, False, False, False]
['after', 'before']
0.5555555555555556 {4, 5} {1, 4}
actTime c017-c153 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c042-c016 [True, False, False, False]
['after', 'before']
1.3333333333333333 {3} {1, 3}
actTime c017-c065 [True, False, False, False]
['before', 'after']
0.3076923076923077 {6, 7} {4}
actTime c017-c065 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c015-c040 [True, False, False, False]
['before', 'after']
0.4166666666666667 {5, 7} {0, 5}
actTime c015-c040 [False, False, False, False]
['after']
1.0 {2} {2}
actTime c015-c044 [True, False, False, False]
['before', 'after']
0.25 {5, 7} {0, 3}
actTime c015-c044 [F

0.6 {2, 3} {0, 3}
actTime c015-c065 [True, False, False, False]
['before', 'after']
0.46153846153846156 {6, 7} {6}
actTime c015-c065 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c094-c110 [False, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c020-c015 [True, False, False, False]
['before', 'after']
1.2857142857142858 {7} {4, 5}
actTime c011-c066 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c066-c059 [False, False, False, False]
['after']
0.0 {1} {0}
actTime c066-c059 [True, False, False, False]
['after', 'before']
0.2857142857142857 {3, 4} {2}
actTime c015-c154 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c153-c084 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c043-c152 [False, False, False, False]
['after', 'before']
1.0 {2} {0, 2}
actTime c007-c151 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c125-c151 [False, False, False, False]
['after', 'befo

1.5 {2} {1, 2}
actTime c057-c151 [False, False, False, False]
['after', 'before']
1.0 {1} {1}
actTime c076-c040 [True, False, False, False]
['before', 'after']
0.38461538461538464 {6, 7} {5}
actTime c076-c040 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c079-c040 [True, False, False, False]
['before', 'after']
1.5 {6} {4, 5}
actTime c087-c151 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c087-c008 [True, False, False, False]
['after', 'before']
1.0 {1, 2} {1, 2}
actTime c087-c008 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c141-c038 [True, False, False, False]
['before', 'after']
0.3333333333333333 {1, 2} {1}
actTime c141-c038 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c073-c008 [True, False, False, False]
['after', 'before']
1.0 {1, 2} {1, 2}
actTime c073-c008 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c009-c154 [False, False, False, False]
['before', 'after']
1.0 {1} {0, 1}
actTime c149-c041 [Tru

actTime c094-c071 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c094-c071 [True, False, False, False]
['after', 'before']
0.6153846153846154 {6, 7} {2, 6}
actTime c094-c070 [True, False, False, False]
['after', 'before']
0.42857142857142855 {7} {3}
actTime c070-c094 [True, False, False, False]
['before', 'after']
1.5 {2} {1, 2}
actTime c126-c078 [False, False, False, False]
['after']
1.0 {1} {1}
actTime c126-c078 [True, False, False, False]
['after', 'before']
0.5454545454545454 {5, 6} {2, 4}
actTime c087-c090 [True, False, False, False]
['after', 'before']
0.3333333333333333 {1, 2} {1}
actTime c087-c090 [False, False, False, False]
['before']
0.0 {1} {0}
actTime c071-c112 [True, False, False, False]
['before', 'after']
0.8333333333333334 {6} {2, 3}
actTime c096-c075 [False, False, False, False]
['after', 'before']
1.0 {1} {0, 1}
actTime c096-c075 [True, False, False, False]
['after', 'before']
1.2 {5} {2, 4}
actTime c074-c075 [True, False, False, False]
['after', 'before'

In [61]:
at = preds[(preds['type'] == 'objTime')]
at.shape

(64, 36)

In [64]:
at.groupby(['indirects']).count()

question  answer  attributes  global  local  \
indirects                                                                   
[False, False, False, False]        18      18          18      18     18   
[True, False, False, False]         40      40          40      40     40   
[True, False, False, True]           6       6           6       6      6   

                              steps  id  metrics  program  sg_grounding  ...  \
indirects                                                                ...   
[False, False, False, False]     18  18       18       18            18  ...   
[True, False, False, False]      40  40       40       40            40  ...   
[True, False, False, True]        6   6        6        6             6  ...   

                              indir_time  vid_id  Total_preds  question_id  \
indirects                                                                    
[False, False, False, False]          18      18           18           18   
[True, False, False, False]           40      40           40           40   
[True, False, False, True]             6       6            6            6   

                              video_name  csv_q_id  words  AGQA_ans  \
indirects                                                             
[False, False, False, False]          18        18     18        18   
[True, False, False, False]           40        40     40        40   
[True, False, False, True]             6         6      6         6   

                              prediction  correct  
indirects                                          
[False, False, False, False]          18       18  
[True, False, False, False]           40       40  
[True, False, False, True]             6        6  

[3 rows x 35 columns]

### By template

In [98]:
templ = preds[(preds['type'] == 'objFirstChoose')]
templ.shape, templ.columns


((27554, 36),
 Index(['question', 'answer', 'attributes', 'global', 'local', 'steps', 'id',
        'metrics', 'program', 'sg_grounding', 'type', 'structural', 'semantic',
        'ans_type', 'video_id', 'novel_comp', 'indirects', 'direct_args',
        'direct_time', 'nc_before', 'nc_first', 'nc_longer', 'nc_objrel',
        'indir_obj', 'indir_rel', 'indir_act', 'indir_time', 'vid_id',
        'Total_preds', 'question_id', 'video_name', 'csv_q_id', 'words',
        'AGQA_ans', 'prediction', 'correct'],
       dtype='object'))

In [105]:
templ2 = templ[(templ['indirects'] == '[False, False, False, False]')]
templ2.groupby(['correct']).count()

question  answer  attributes  global  local  steps    id  metrics  \
correct                                                                      
0            1315    1315        1315    1315   1315   1315  1315     1315   
1            1148    1148        1148    1148   1148   1148  1148     1148   

         program  sg_grounding  ...  indir_act  indir_time  vid_id  \
correct                         ...                                  
0           1315          1315  ...       1315        1315    1315   
1           1148          1148  ...       1148        1148    1148   

         Total_preds  question_id  video_name  csv_q_id  words  AGQA_ans  \
correct                                                                    
0               1315         1315        1315      1315   1315      1315   
1               1148         1148        1148      1148   1148      1148   

         prediction  
correct              
0              1315  
1              1148  

[2 rows x 35 columns]

In [107]:
print("objFirstChoose")
print('%s Correct [F,F,F,F]' % round((1148 / (1148 + 1315)), 2))
print('%s Correct [T,F,F,F]' % round((1595 / (2950 + 1595)), 2))
print('%s Correct [F,F,F,T]' % round((1509 / (1509 + 1625)), 2))
print('%s Correct [T,F,F,T]' % round((6823 / (6823 + 10398)), 2))
print()
print("objLastChoose")
print('%s Correct [F,F,F,F]' % round((2449 / (2068 + 2449)), 2))
print('%s Correct [T,F,F,F]' % round((3201 / (1758 + 3201)), 2))
print('%s Correct [F,F,F,T]' % round((2257 / (2257 + 2003)), 2))
print('%s Correct [T,F,F,T]' % round((9426 / (9426 + 9193)), 2))

objFirstChoose
0.47 Correct [F,F,F,F]
0.35 Correct [T,F,F,F]
0.48 Correct [F,F,F,T]
0.4 Correct [T,F,F,T]

objLastChoose
0.54 Correct [F,F,F,F]
0.65 Correct [T,F,F,F]
0.53 Correct [F,F,F,T]
0.51 Correct [T,F,F,T]


In [83]:
x = exists.groupby(['local', 'type', 'answer']).count()

In [84]:
with open('../Testtt.csv', 'w+') as f:
    x.to_csv(f)

In [125]:
args = ba.T.to_dict().values()

In [122]:
org2 = org.copy()

In [126]:
org = {}

for i in args:
    indir = i['indirects']
    
        
    t = i['type']
    a = i['direct_args']
    ans = i['answer']
    
    if t not in org:
        org[t] = {}
    if a not in org[t]:
        org[t][a] = {}
    if indir not in org[t][a]:
        org[t][a][indir] = {}
    if ans not in org[t][a][indir]:
        org[t][a][indir][ans] = {'answer': 0, 'correct': 0}
    org[t][a][indir][ans]['answer'] += 1
    if i['correct']:
        org[t][a][indir][ans]['correct'] += 1

In [116]:
org = {}

for v_id in test_stsgs:#args:
    with open('../exports/dataset/balanced/test/%s.txt' % v_id, 'rb') as f:
        QA = json.load(f)
    
    
    for q_id in QA:
        i = QA[q_id]
        unf_indir = i['metrics']['indirects']
        
        indir = ''
        
        for ind in unf_indir:
            indir += str(ind)
            indir += '-'


        t = i['attributes']['type']
        if t not in ['relTime', 'actTime']:
            continue
        a = i['metrics']['direct_args']
        ans = i['answer']

        if t not in org:
            org[t] = {}
        if a not in org[t]:
            org[t][a] = {}
        if indir not in org[t][a]:
            org[t][a][indir] = {}
        if ans not in org[t][a][indir]:
            org[t][a][indir][ans] = {'answer': 0, 'correct': 0}
        org[t][a][indir][ans]['answer'] += 1
        #if i['correct']:
        #    org[t][a][indir][ans]['correct'] += 1

In [118]:
for i in org:
    print(i)

relTime
actTime


In [127]:
num_eq = 0
num_uneq = 0

for t in ['relTime']:#org:
    for ar in org[t]:
        for indir in org[t][ar]:
            lens_ans = set()
            lens_cor = set()
            answers = []
            for ans in org[t][ar][indir]:
                lens_ans.add(org[t][ar][indir][ans]['answer'])
                lens_cor.add(org[t][ar][indir][ans]['correct'])
                answers.append(ans)

            
            tot_ans = 0
            tot_cor = 0
            for i in lens_ans:
                tot_ans += i
            for i in lens_cor:
                tot_cor += i
            perc = tot_cor / tot_ans
                
            if len(lens_ans) != 1:
                num_uneq += tot_ans
                continue
                print(t, ar, indir)
                print(answers)
                print(perc, lens_ans, lens_cor)
                
            else:
                num_eq += tot_ans
                

print('UNEQUAL AMOUNTS: %s questions' % num_uneq)
print('EQUAL AMOUNTS: %s questions' % num_eq)

# So there are more local dists with equal, but more questions in unequal

# but firstchoose also has many unequal amounts and its fine...

UNEQUAL AMOUNTS: 22750 questions
EQUAL AMOUNTS: 8652 questions


In [128]:
choose = preds[preds['structural'] == 'choose']

choose.shape

(98314, 36)

In [131]:


choose.groupby(['type', 'indirects']).count()

question  answer  attributes  \
type           indirects                                                    
objFirstChoose [False, False, False, False]      2463    2463        2463   
               [False, False, False, True]       3134    3134        3134   
               [False, False, True, True]          79      79          79   
               [True, False, False, False]       4553    4553        4553   
               [True, False, False, True]       17221   17221       17221   
               [True, False, True, True]          104     104         104   
objLastChoose  [False, False, False, False]      4517    4517        4517   
               [False, False, False, True]       4260    4260        4260   
               [False, False, True, True]         132     132         132   
               [True, False, False, False]       4959    4959        4959   
               [True, False, False, True]       18619   18619       18619   
               [True, False, True, True]           95      95          95   
objWhatChoose  [False, False, False, False]      1351    1351        1351   
               [False, False, False, True]      11515   11515       11515   
               [False, False, True, True]          94      94          94   
               [True, False, False, False]       1133    1133        1133   
               [True, False, False, True]       24030   24030       24030   
               [True, False, True, True]           55      55          55   

                                             global  local  steps     id  \
type           indirects                                                   
objFirstChoose [False, False, False, False]    2463   2463   2463   2463   
               [False, False, False, True]     3134   3134   3134   3134   
               [False, False, True, True]        79     79     79     79   
               [True, False, False, False]     4553   4553   4553   4553   
               [True, False, False, True]     17221  17221  17221  17221   
               [True, False, True, True]        104    104    104    104   
objLastChoose  [False, False, False, False]    4517   4517   4517   4517   
               [False, False, False, True]     4260   4260   4260   4260   
               [False, False, True, True]       132    132    132    132   
               [True, False, False, False]     4959   4959   4959   4959   
               [True, False, False, True]     18619  18619  18619  18619   
               [True, False, True, True]         95     95     95     95   
objWhatChoose  [False, False, False, False]    1351   1351   1351   1351   
               [False, False, False, True]    11515  11515  11515  11515   
               [False, False, True, True]        94     94     94     94   
               [True, False, False, False]     1133   1133   1133   1133   
               [True, False, False, True]     24030  24030  24030  24030   
               [True, False, True, True]         55     55     55     55   

                                             metrics  program  sg_grounding  \
type           indirects                                                      
objFirstChoose [False, False, False, False]     2463     2463          2463   
               [False, False, False, True]      3134     3134          3134   
               [False, False, True, True]         79       79            79   
               [True, False, False, False]      4553     4553          4553   
               [True, False, False, True]      17221    17221         17221   
               [True, False, True, True]         104      104           104   
objLastChoose  [False, False, False, False]     4517     4517          4517   
               [False, False, False, True]      4260     4260          4260   
               [False, False, True, True]        132      132           132   
               [True, False, False, False]      4959     4959          4959   
               [True, False, False,

FRom before: 
UNEQUAL AMOUNTS: 22750 questions
EQUAL AMOUNTS: 8652 questions

Frm new balanced: 

UNEQUAL AMOUNTS: 16128 questions
EQUAL AMOUNTS: 11918 questions


So def getting better -- probably worth. 

Just smooth then?


In [89]:
from collections import OrderedDict

In [95]:


def getBinaryCat(q):
    #g = q['global']

    t = q['attributes']['type']

    # first find local
    #if t in ['objLastChoose', 'objFirstChoose', 'objWhatChoose', 'actLengthLongerChoose', 'actLengthShorterChoose']:
        #local = q['direct']
        # would still be local? b/c other two in answer
    if t == 'actCountChooseMore':
        local = "more"
    elif t == 'actCountChooseFewer':
        local = 'fewer'
    elif t == 'actLengthLongerChoose':
        local = 'longer'
    elif t == 'actLengthShorterChoose':
        local = 'shorter'
    else: 
        local = q['local']


    # then find answers
    a = q['answer']
    if a == "Yes" or a == "No":
        ans = 'yes-no'
    elif a == 'before' or a == 'after':
        ans = 'before-after'
    elif t in ['actCountChooseMore', 'actCountChooseFewer', 'actLengthLongerChoose', 'actLengthShorterChoose']:
        ans = q['local']
    else:
        ans = q['metrics']['direct_args']

    time0, time1 = q['metrics']['direct_time']
    

    category = "%s-%s-%s-%s" % (ans, local, time0, time1)
    
    return category


In [96]:
locs = {}
for i, v_id in enumerate(test_stsgs):
    if i % 300 == 0:
        print(i)
    with open('../exports/dataset_new/balanced/test/%s.txt' % v_id, 'rb') as f:
        QA = json.load(f)
        
    for q_id in QA:
        q = QA[q_id]
        if 'exists' not in q['global']:
            continue
        l = getBinaryCat(q)
        a = q['answer']
        
        if l not in locs:
            locs[l] = {'Yes': 0, 'No': 0}
        locs[l][a] += 1

0
300
600
900
1200
1500
1800


In [99]:
for i in locs:
    j = locs[i]
    
    if j['Yes'] != 0 and j['No'] != 0:
        print(i, j)

In [209]:
locs_sm = {}
this_loc = {}
for i, v_id in enumerate(test_stsgs):
    if i % 300 == 0:
        print(i)
    with open('../exports/dataset_new/smoothed/test/%s.txt' % v_id, 'rb') as f:
        QA = json.load(f)
        
    for q_id in QA:
        q = QA[q_id]
        if 'exists' not in q['global']:
            continue
        l = getBinaryCat(q)
        a = q['answer']
        
        if l not in locs_sm:
            locs_sm[l] = {'Yes': 0, 'No': 0}
        locs_sm[l][a] += 1
        #this_loc[q_id] = q

0
300
600
900
1200
1500
1800


In [156]:
for i in locs_sm:
    j = locs_sm[i]
    continue
    
    if j['Yes'] != j['No']:
        print(i, j)
        
    continue
    if j['Yes'] != 0 and j['No'] != 0:
        print(i, j)

NameError: name 'locs_sm' is not defined

In [102]:
path = '../exports/%s/other_formats/%s-%s-agqa.csv' % ('dataset_new', 'test', 'balanced')
with open(path, 'rb') as f:
    test = pd.read_csv(f)
    
path = '../exports/%s/other_formats/%s-%s-agqa.csv' % ('dataset_new', 'train', 'balanced')
with open(path, 'rb') as f:
    train = pd.read_csv(f)
    
    
test.shape, train.shape

((1763020, 28), (1181289, 28))

In [121]:
train_bqt = pickleLoad("../exports/%s/by_q_type/binary/train-0-%s.pkl" % ('dataset_new', len(train_stsgs)))

In [201]:
for i in train_bqt['exists']['all']:
    print(i)
    for j in train_bqt['exists']['all'][i]:
        print()
        for k in train_bqt['exists']['all'][i][j]:
            print(k, len(train_bqt['exists']['all'][i][j][k]))
        print(j,  train_bqt['exists']['all'][i][j])
    break

yes-no-o17-before-c092

no_temporal 0
same_ans 57
diff_ans 0
no_direct 0
Yes {'no_temporal': [], 'same_ans': ['46GP8-0', 'XV8CH-2', 'XV8CH-1782', 'XV8CH-1783', 'YUEB9-22', 'YUEB9-14334', 'X0O65-1', 'X0O65-880', 'X0O65-881', 'S8TI7-14', '406LH-0', 'DTJS6-17', 'Q49E0-0', 'Q49E0-8978', 'Q49E0-8979', 'Q49E0-8980', 'Q49E0-8981', 'N8XDV-192', 'R4ENI-16793', 'R4ENI-16794', 'R4ENI-16795', 'LZUAY-0', 'LZUAY-1', 'M7Y6V-36', 'GTK8W-51', 'E75C2-10', 'KCEJF-0', 'KCEJF-1052', 'KCEJF-1053', 'KS5VD-0', 'GKSL2-135', 'GKSL2-56476', 'GKSL2-56477', '83V0A-2', '59CDL-0', 'PE4BQ-9', 'PE4BQ-10', 'PE4BQ-1297', 'BB8Q0-83', 'JIWY2-1', 'JIWY2-5519', 'JIWY2-5520', 'JIWY2-5521', 'PQBGG-3', 'PQBGG-13415', 'GN4SJ-4', 'QUGSS-0', 'PP2FF-0', 'PP2FF-12016', 'PP2FF-12017', '7VP2U-1', '7VP2U-17590', '7VP2U-17591', '7VP2U-17592', 'XAW3U-1', 'XAW3U-1715', 'XAW3U-1716'], 'diff_ans': [], 'no_direct': []}

no_temporal 0
same_ans 406
diff_ans 16
no_direct 0
No {'no_temporal': [], 'same_ans': ['MD41D-210', 'U1DTW-100', 'U1DTW-10

In [126]:


BINARY_GLOBAL_IDS = ['exists', 'first', 'last', 'time', 'length', 'what', 'count']
OPEN_GLOBAL_IDS = ['first', 'last', 'what', 'count', 'length', 'count-int']


In [128]:


def balanceLocalBny(local_binary, b, mn):
    """ balances a distribution for questions of a given attribute

    Args:
        loc_bin: a dictionary mapping local values to quesiton ids

    Returns:
        og_dist: origional answer distribution
        up_dist: updated answer distribution
        keep: 
        delete: 
    """

    og_dist, head, tail = createOrigionalDist(local_binary)
    ## TAKING THIS OUT FOR SIMPLICITY"
    # P = og_dist.copy()
    #up_dist, delete, total = balance5(P, head, tail, b, mn, 1, True)

    if len(og_dist) != 2:
        #print("HAVE A PROBLEM")
        # return deleteing everything
        if len(og_dist) == 0:
            print("Weird - og dist has 0 things in it")
            return
        #print("og_dist", og_dist)
        a1, cnt1 = og_dist[0]
        #print("a, cnt", a1, cnt1)
        delete = {
            a1: cnt1,
        }
        og_dist = [og_dist[0], ("placement", 0)]
        up_dist = [(a1, 0), ("placement", 0)]

        return og_dist, up_dist, delete, -1
    # (a1, cnt1), (a2, cnt2)
    (a1, cnt1), (a2, cnt2) = og_dist
    if cnt1 > cnt2:
        # do something
        delete = {
            a1: cnt1 - cnt2,
            a2: 0
        }
        up_dist = [(a1, cnt2), (a2, cnt2)]
    elif cnt2 > cnt1:
        delete = {
            a2: cnt2 - cnt1,
            a1: 0
        }
        up_dist = [(a1, cnt1), (a2, cnt1)]
        #do something
        
    else:
        delete = {
            a1: 0,
            a2: 0
        }
        up_dist = [(a1, cnt1), (a2, cnt2)]

    #print(og_dist, up_dist, delete)
    return og_dist, up_dist, delete, -1


In [135]:

def createOrigionalDist(dic):
    counts = getValueCount(dic)
    sort = sortDictOfCounts(counts)
    P = []
    head = 0  # sum_{j \leq i} c_j
    tail = 0
    for i in sort:
        P.append((i, counts[i]))
        tail = tail + counts[i]
    return P, head, tail


In [138]:

def getValueCount(dic):
    cnt = {}
    for i in dic:
        tot = 0
        ##print("dic[i]", dic[i])
        #print("i", i)
        for tt in dic[i]:
            #print("tt", tt)
            tot += len(dic[i][tt])
        cnt[i] = tot
    return cnt


def sortDictOfCounts(dic):
    return sorted(dic, key=dic.__getitem__)[::-1]


In [140]:
glob_idx = 0

bny = train_bqt

########
up = {}
og = {}
q_ids_to_delete = []

# TODO could probs move out the creating binary dict
for glob in BINARY_GLOBAL_IDS:
    up[glob] = {}
    og[glob] = {}

all_binary_cat = ['all']#['Yes/No', 'before/after']
for glob in up:
    for cat in all_binary_cat:
        up[glob][cat] = {}
        og[glob][cat] = {}

glob = BINARY_GLOBAL_IDS[glob_idx]
num_to_del = 0
for cat in bny[glob]:
    for loc in bny[glob][cat]:
        og_dist, up_dist, delete, total = balanceLocalBny(bny[glob][cat][loc], 1, 0)
        #print()
        ##print('og', og_dist)
        #print('up', up_dist)
        #print('del', delete)

        if up_dist == "illegal":
            og[glob][cat][loc] = []
            up[glob][cat][loc] = []
            continue
        print(loc, og_dist, up_dist)
        #print('og', og, 'glob', glob, 'cat', cat, 'loc', loc)
        og[glob][cat][loc] = og_dist
        up[glob][cat][loc] = up_dist
        
        continue
        #print()
        #print(cat, loc)
        #print("og dist", og_dist)
        #print("up dist", up_dist)
        for ans in delete:
            cnt = delete[ans]
            #print("to delete", delete[ans])
            #print("choices", len(set(random.choices(bny[glob][cat][loc][ans], k=cnt))))
            #print("samples", len(set(random.sample(bny[glob][cat][loc][ans], k=cnt))))
            #q_ids_to_delete.append(random.sample(bny[glob][cat][loc][ans], k=cnt)) 
            q_ids_to_delete.append(bs.getIdsToDelete(bny[glob][cat][loc][ans], cnt)) 
            num_to_del = num_to_del + cnt
            #q_ids_to_delete = q_ids_to_delete + random.choices(bny[glob][cat][loc][ans], k=cnt)
print(glob_idx, " deleted ", num_to_del)
#if delete_from_QA:
#    for q_ids in q_ids_to_delete:

yes-no-o17-before-c092 [('No', 422), ('Yes', 57)] [('No', 57), ('Yes', 57)]
yes-no-o17-while-c092 [('No', 728), ('Yes', 86)] [('No', 86), ('Yes', 86)]
yes-no-o17-all- [('No', 5722), ('Yes', 1829)] [('No', 1829), ('Yes', 1829)]
yes-no-o36-after-c066 [('No', 200), ('Yes', 4)] [('No', 4), ('Yes', 4)]
yes-no-o36-while-c066 [('No', 444), ('Yes', 2)] [('No', 2), ('Yes', 2)]
yes-no-o36-all- [('No', 7513), ('Yes', 274)] [('No', 274), ('Yes', 274)]
yes-no-o23-before-c092 [('No', 450), ('Yes', 35)] [('No', 35), ('Yes', 35)]
yes-no-o23-after-c066 [('No', 189), ('Yes', 13)] [('No', 13), ('Yes', 13)]
yes-no-o23-while-c092 [('No', 778), ('Yes', 43)] [('No', 43), ('Yes', 43)]
yes-no-o23-while-c066 [('No', 419), ('Yes', 23)] [('No', 23), ('Yes', 23)]
yes-no-o23-all- [('No', 6529), ('Yes', 1041)] [('No', 1041), ('Yes', 1041)]
yes-no-o27-before-c092 [('No', 432), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-o27-after-c066 [('No', 128), ('Yes', 42)] [('No', 42), ('Yes', 42)]
yes-no-o27-while-c0

yes-no-o19-before-c099 [('No', 454), ('Yes', 17)] [('No', 17), ('Yes', 17)]
yes-no-o19-after-c075 [('No', 192), ('Yes', 10)] [('No', 10), ('Yes', 10)]
yes-no-o19-after-c153 [('No', 459), ('Yes', 22)] [('No', 22), ('Yes', 22)]
yes-no-o19-after-c127 [('No', 562), ('Yes', 16)] [('No', 16), ('Yes', 16)]
yes-no-o19-after-c100 [('No', 459), ('Yes', 9)] [('No', 9), ('Yes', 9)]
yes-no-o19-while-c098 [('No', 1309), ('Yes', 56)] [('No', 56), ('Yes', 56)]
yes-no-o19-while-c075 [('No', 381), ('Yes', 10)] [('No', 10), ('Yes', 10)]
yes-no-o19-while-c153 [('No', 659), ('Yes', 31)] [('No', 31), ('Yes', 31)]
yes-no-o19-while-c127 [('No', 1203), ('Yes', 31)] [('No', 31), ('Yes', 31)]
yes-no-o19-while-c100 [('No', 556), ('Yes', 19)] [('No', 19), ('Yes', 19)]
yes-no-o19-while-c099 [('No', 465), ('Yes', 22)] [('No', 22), ('Yes', 22)]
yes-no-o19-between-c075-c099 [('No', 2), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-o19-between-c153-c099 [('No', 6), ('Yes', 1)] [('No', 1), ('Yes', 1)]
yes-no-o1

yes-no-r13-between-c127-c099 [('No', 17), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-r13-between-c100-c099 [('No', 71), ('Yes', 1)] [('No', 1), ('Yes', 1)]
yes-no-v026-before-c098 [('No', 406), ('Yes', 324)] [('No', 324), ('Yes', 324)]
yes-no-v026-before-c153 [('No', 487), ('Yes', 49)] [('No', 49), ('Yes', 49)]
yes-no-v026-before-c100 [('No', 273), ('Yes', 149)] [('No', 149), ('Yes', 149)]
yes-no-v026-before-c099 [('No', 288), ('Yes', 183)] [('No', 183), ('Yes', 183)]
yes-no-v026-after-c153 [('No', 436), ('Yes', 45)] [('No', 45), ('Yes', 45)]
yes-no-v026-after-c100 [('No', 303), ('Yes', 165)] [('No', 165), ('Yes', 165)]
yes-no-v026-while-c098 [('No', 817), ('Yes', 548)] [('No', 548), ('Yes', 548)]
yes-no-v026-while-c153 [('No', 634), ('Yes', 56)] [('No', 56), ('Yes', 56)]
yes-no-v026-while-c100 [('No', 384), ('Yes', 191)] [('No', 191), ('Yes', 191)]
yes-no-v026-while-c099 [('No', 329), ('Yes', 158)] [('No', 158), ('Yes', 158)]
yes-no-v026-between-c153-c099 [('No', 4), ('Yes

yes-no-c000-after-c153 [('No', 425), ('Yes', 20)] [('No', 20), ('Yes', 20)]
yes-no-c000-after-c127 [('No', 539), ('Yes', 32)] [('No', 32), ('Yes', 32)]
yes-no-c000-after-c100 [('No', 456), ('Yes', 12)] [('No', 12), ('Yes', 12)]
yes-no-c000-while-c098 [('No', 1327), ('Yes', 38)] [('No', 38), ('Yes', 38)]
yes-no-c000-while-c075 [('No', 361), ('Yes', 27)] [('No', 27), ('Yes', 27)]
yes-no-c000-while-c153 [('No', 610), ('Yes', 28)] [('No', 28), ('Yes', 28)]
yes-no-c000-while-c127 [('No', 1134), ('Yes', 91)] [('No', 91), ('Yes', 91)]
yes-no-c000-while-c100 [('No', 563), ('Yes', 12)] [('No', 12), ('Yes', 12)]
yes-no-c000-while-c099 [('No', 477), ('Yes', 10)] [('No', 10), ('Yes', 10)]
yes-no-c000-between-c075-c099 [('No', 2), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c000-between-c153-c099 [('No', 7), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c000-between-c127-c099 [('No', 17), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c000-between-c100-c099 [('No', 70), 

yes-no-c023-before-c098 [('No', 636), ('Yes', 12)] [('No', 12), ('Yes', 12)]
yes-no-c023-before-c153 [('No', 244), ('Yes', 17)] [('No', 17), ('Yes', 17)]
yes-no-c023-before-c100 [('No', 412), ('Yes', 10)] [('No', 10), ('Yes', 10)]
yes-no-c023-before-c099 [('No', 348), ('Yes', 4)] [('No', 4), ('Yes', 4)]
yes-no-c023-after-c075 [('No', 146), ('Yes', 2)] [('No', 2), ('Yes', 2)]
yes-no-c023-after-c153 [('No', 236), ('Yes', 11)] [('No', 11), ('Yes', 11)]
yes-no-c023-after-c127 [('No', 407), ('Yes', 14)] [('No', 14), ('Yes', 14)]
yes-no-c023-after-c100 [('No', 465), ('Yes', 3)] [('No', 3), ('Yes', 3)]
yes-no-c023-while-c098 [('No', 910), ('Yes', 19)] [('No', 19), ('Yes', 19)]
yes-no-c023-while-c075 [('No', 259), ('Yes', 3)] [('No', 3), ('Yes', 3)]
yes-no-c023-while-c153 [('No', 320), ('Yes', 10)] [('No', 10), ('Yes', 10)]
yes-no-c023-while-c127 [('No', 839), ('Yes', 33)] [('No', 33), ('Yes', 33)]
yes-no-c023-while-c100 [('No', 568), ('Yes', 7)] [('No', 7), ('Yes', 7)]
yes-no-c023-while-c099 

...

yes-no-c046-between-c023-c009 [('No', 4), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c023-c062 [('No', 11), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c063-c006 [('No', 11), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c063-c097 [('No', 10), ('Yes', 1)] [('No', 1), ('Yes', 1)]
yes-no-c046-between-c063-c141 [('No', 6), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c063-c020 [('No', 8), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c063-c009 [('No', 17), ('Yes', 1)] [('No', 1), ('Yes', 1)]
yes-no-c046-between-c063-c062 [('No', 100), ('Yes', 1)] [('No', 1), ('Yes', 1)]
yes-no-c046-between-c002-c006 [('No', 22), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c002-c061 [('No', 2), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c002-c097 [('No', 15), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c046-between-c002-c141 [('No', 

yes-no-c021-before-c141 [('No', 230), ('Yes', 8)] [('No', 8), ('Yes', 8)]
yes-no-c021-before-c020 [('No', 994), ('Yes', 418)] [('No', 418), ('Yes', 418)]
yes-no-c021-before-c000 [('No', 782), ('Yes', 125)] [('No', 125), ('Yes', 125)]
yes-no-c021-before-c023 [('No', 688), ('Yes', 157)] [('No', 157), ('Yes', 157)]
yes-no-c021-before-c009 [('No', 367), ('Yes', 46)] [('No', 46), ('Yes', 46)]
yes-no-c021-before-c063 [('No', 1071), ('Yes', 226)] [('No', 226), ('Yes', 226)]
yes-no-c021-before-c002 [('No', 655), ('Yes', 100)] [('No', 100), ('Yes', 100)]
yes-no-c021-before-c062 [('No', 1191), ('Yes', 319)] [('No', 319), ('Yes', 319)]
yes-no-c021-after-c061 [('No', 1211), ('Yes', 155)] [('No', 155), ('Yes', 155)]
yes-no-c021-after-c155 [('No', 76), ('Yes', 8)] [('No', 8), ('Yes', 8)]
yes-no-c021-after-c000 [('No', 824), ('Yes', 52)] [('No', 52), ('Yes', 52)]
yes-no-c021-after-c023 [('No', 712), ('Yes', 425)] [('No', 425), ('Yes', 425)]
yes-no-c021-after-c009 [('No', 340), ('Yes', 25)] [('No', 25

yes-no-c025-between-c002-c097 [('No', 16), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c025-between-c002-c141 [('No', 12), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c025-between-c002-c020 [('No', 5), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c025-between-c002-c023 [('No', 4), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c025-between-c002-c009 [('No', 10), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c025-between-c002-c063 [('No', 4), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c025-between-c002-c062 [('No', 5), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c017-before-c097 [('No', 485), ('Yes', 24)] [('No', 24), ('Yes', 24)]
yes-no-c017-before-c141 [('No', 197), ('Yes', 9)] [('No', 9), ('Yes', 9)]
yes-no-c017-before-c020 [('No', 1053), ('Yes', 31)] [('No', 31), ('Yes', 31)]
yes-no-c017-before-c023 [('No', 640), ('Yes', 18)] [('No', 18), ('Yes', 18)]
yes-no-c017-before-c063 [('No', 2127), ('Yes', 60)] [('No', 6

yes-no-c067-between-c155-c063 [('No', 11), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c155-c062 [('No', 11), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c006 [('No', 21), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c061 [('No', 16), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c097 [('No', 48), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c141 [('No', 17), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c020 [('No', 17), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c009 [('No', 34), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c063 [('No', 16), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c000-c062 [('No', 11), ('placement', 0)] [('No', 0), ('placement', 0)]
yes-no-c067-between-c023-c006 [('No', 14), ('placement', 0)] [('No', 0), ('placement', 0)]

KeyboardInterrupt: 

In [159]:
d_path = 'dataset_new'
up = pickleLoad("../exports/%s/distributions/%s-binary-up-%s.pkl" % (d_path, group, BINARY_GLOBAL_IDS[0]))

In [160]:
up

{'exists': {'all': {'yes-no-o17-before-c092': [('No', 57), ('Yes', 57)],
   'yes-no-o17-while-c092': [('No', 86), ('Yes', 86)],
   'yes-no-o17-all-': [('No', 1829), ('Yes', 1829)],
   'yes-no-o36-after-c066': [('No', 4), ('Yes', 4)],
   'yes-no-o36-while-c066': [('No', 2), ('Yes', 2)],
   'yes-no-o36-all-': [('No', 274), ('Yes', 274)],
   'yes-no-o23-before-c092': [('No', 35), ('Yes', 35)],
   'yes-no-o23-after-c066': [('No', 13), ('Yes', 13)],
   'yes-no-o23-while-c092': [('No', 43), ('Yes', 43)],
   'yes-no-o23-while-c066': [('No', 23), ('Yes', 23)],
   'yes-no-o23-all-': [('No', 1041), ('Yes', 1041)],
   'yes-no-o27-before-c092': [('No', 0), ('placement', 0)],
   'yes-no-o27-after-c066': [('No', 42), ('Yes', 42)],
   'yes-no-o27-while-c092': [('No', 1), ('Yes', 1)],
   'yes-no-o27-while-c066': [('No', 36), ('Yes', 36)],
   'yes-no-o27-all-': [('No', 251), ('Yes', 251)],
   'yes-no-o3-before-c092': [('No', 68), ('Yes', 68)],
   'yes-no-o3-after-c066': [('No', 3), ('Yes', 3)],
   'yes

# Hello

so, it is equal in the binary up. however I accidentally dumped up! and it needs to not. Going to re bin bal


next check if the q_ids to delete works well

also -- why it's not saving as having the new binary split!

ok it now has the updated binary categories..

In [157]:
d_path = 'dataset_new'
og = pickleLoad("../exports/%s/distributions/%s-binary-og-%s.pkl" % (d_path, group, BINARY_GLOBAL_IDS[0]))

In [158]:
og

{'exists': {'all': {}},
 'first': {'all': {'r22-o4-o26-r22-o4-o26': [('blanket', 121),
    ('placement', 0)],
   'r22-o26-o4-r22-o26-o4': [('pillow', 153), ('blanket', 61)],
   'yes-no-r22-o4': [('No', 1280), ('Yes', 330)],
   'yes-no-r22-o26': [('No', 402), ('Yes', 114)],
   'yes-no-r8-o4': [('No', 4106), ('Yes', 1491)],
   'yes-no-r6-o4': [('No', 4390), ('Yes', 1115)],
   'yes-no-r6-o26': [('No', 1220), ('Yes', 134)],
   'yes-no-r22': [('No', 14539), ('Yes', 3579)],
   'r22-o35-o36-r22-o35-o36': [('window', 31), ('placement', 0)],
   'r22-o36-o8-r22-o36-o8': [('window', 73), ('chair', 2)],
   'r22-o8-o36-r22-o8-o36': [('chair', 38), ('window', 13)],
   'r8-o35-o36-r8-o35-o36': [('window', 30), ('vacuum', 12)],
   'r6-o36-o8-r6-o36-o8': [('window', 37), ('chair', 9)],
   'r6-o8-o12-r6-o8-o12': [('dish', 133), ('chair', 57)],
   'r6-o8-o36-r6-o8-o36': [('chair', 31), ('window', 12)],
   'r6-o12-o8-r6-o12-o8': [('dish', 109), ('chair', 31)],
   'r6-o36-o12-r6-o36-o12': [('window', 46), 

In [161]:
d_path = 'dataset_new'
to_del = pickleLoad("../exports/%s/q_ids_to_delete/%s-binary-%s.pkl" % (d_path, group, BINARY_GLOBAL_IDS[0]))

In [162]:
type(to_del)

list

In [163]:
to_del[0]

[[],
 ['LZ2Y4-251',
  'E002I-47071',
  'TYWHY-270',
  'C10FA-688',
  '7EJUR-178',
  'XMYXI-35642',
  'AAQHJ-1250',
  'BJ7YW-9415',
  '13XM4-354',
  'ALJ7B-14062',
  'SUG5S-258',
  '3MSZA-103',
  '2ADJI-256',
  'QZZPS-250',
  'QI0EL-9091',
  'Y4GHN-10656',
  'ZC017-600',
  '5DFKT-8572',
  'SV6KF-6711',
  'TNDT2-648',
  'RLQ9K-128',
  'BHXEI-12261',
  'FDDDG-10364',
  'MSVWC-295',
  '4UXE3-203',
  'T9N9R-13887',
  '1XOQ8-213',
  'LRJKT-718',
  'REWLB-235',
  'P5YNX-7824',
  'Z4Y04-130',
  'PLXUA-92',
  'GCI2J-9472',
  'F66WG-495',
  '15RTV-299',
  'OU3XH-533',
  'O7YEF-5630',
  'H411A-9691',
  '12XD3-112',
  'YPRUL-405',
  'XE19C-341',
  '3LIGG-3498',
  'LXEPT-1128',
  'TH3M0-772',
  'OE243-565',
  'KV6V8-2758',
  'KQ6XW-80668',
  'JCT0K-127',
  'NBMH9-3401',
  'E8JEJ-4671',
  'DWH0T-12673',
  '3OLX3-136',
  '1P7GJ-5638',
  'AFCDN-289',
  'FQS5V-13908',
  'VIN5T-269',
  'J7BOV-301',
  'YQT32-186',
  'OETY6-447',
  'B0XI9-11759',
  'J9T5D-126526',
  'KTXSD-176',
  '4BIMI-27506',
  'BW2OT-

In [192]:
tot = 0
for lst in to_del:
    if len(lst) != 4:
            
        print(len(lst))
    for l in lst:
        tot += len(l)
tot

28732528

# why no exists

In [31]:
by_t = {}
for i, v_id in enumerate(test_stsgs):
    if i % 300 == 0:
        print(i)
    with open('../exports/dataset/smoothed/test/%s.txt' % v_id, 'rb') as f:
        QA = json.load(f)
        
        
    for q_id in QA:
        t = QA[q_id]['attributes']['type']
        
        if t not in by_t:
            by_t[t] = 0
        by_t[t] += 1

0
300
600
900
1200
1500
1800


In [61]:
by_t_bal = {}
for i, v_id in enumerate(test_stsgs):
    if i % 300 == 0:
        print(i)
    with open('../exports/dataset/balanced/test/%s.txt' % v_id, 'rb') as f:
        QA = json.load(f)
        
        
    for q_id in QA:
        t = QA[q_id]['attributes']['type']
        
        if t not in by_t_bal:
            by_t_bal[t] = 0
        by_t_bal[t] += 1

0
300
600
900
1200
1500
1800


In [33]:
by_t

{'objExists': 341640,
 'objRelExists': 721554,
 'relExists': 553260,
 'actExists': 1063414,
 'objWhatGeneral': 2651,
 'objWhat': 238003,
 'objWhatChoose': 105884,
 'objFirst': 24333,
 'objFirstChoose': 27554,
 'objFirstVerify': 210978,
 'actFirst': 587,
 'objLast': 40245,
 'objLastVerify': 113680,
 'relTime': 48832,
 'andObjRelExists': 1080086,
 'xorObjRelExists': 935498,
 'objLastChoose': 37098,
 'actLengthLongerChoose': 3258,
 'actLengthShorterChoose': 3258,
 'actLengthLongerVerify': 3258,
 'actLengthShorterVerify': 3258,
 'actTime': 79786,
 'actLongest': 315,
 'actWhatAfterAll': 306,
 'objTime': 64,
 'actLast': 142,
 'actWhatBefore': 137,
 'actShortest': 53}

In [63]:
by_t_bal # THis is by addapting it

{'objWhatGeneral': 2651,
 'objWhat': 238003,
 'objFirst': 24333,
 'objFirstChoose': 27554,
 'objFirstVerify': 19230,
 'actFirst': 587,
 'objLast': 40245,
 'relTime': 39550,
 'objLastVerify': 17260,
 'objWhatChoose': 38178,
 'objLastChoose': 32582,
 'actLengthLongerChoose': 3258,
 'actLengthShorterChoose': 3258,
 'actLengthLongerVerify': 3258,
 'actLengthShorterVerify': 3258,
 'actTime': 40030,
 'actLongest': 315,
 'actWhatAfterAll': 306,
 'objTime': 64,
 'actLast': 142,
 'actWhatBefore': 137,
 'actShortest': 53,
 'objRelExists': 15338,
 'objExists': 15338,
 'andObjRelExists': 15340,
 'xorObjRelExists': 15340,
 'relExists': 15338,
 'actExists': 15338}

In [64]:
tot = 0 

for i in by_t_bal:
    tot += by_t_bal[i]
    
tot

626284

In [34]:
by_t_bal

{'objWhatGeneral': 2651,
 'objWhat': 238003,
 'objWhatChoose': 26300,
 'objFirst': 24333,
 'objFirstChoose': 27554,
 'actFirst': 587,
 'objLast': 40245,
 'relTime': 39002,
 'objLastChoose': 31860,
 'actLengthLongerChoose': 3258,
 'actLengthShorterChoose': 3258,
 'actLengthLongerVerify': 3258,
 'actLengthShorterVerify': 3258,
 'actTime': 36862,
 'actLongest': 315,
 'actWhatAfterAll': 306,
 'objTime': 64,
 'actLast': 142,
 'actWhatBefore': 137,
 'actShortest': 53}

In [18]:
by_t_bal

{'objWhatGeneral': 2651,
 'objWhat': 238003,
 'objFirst': 24333,
 'objFirstChoose': 27554,
 'actFirst': 587,
 'objLast': 40245,
 'relTime': 39386,
 'objWhatChoose': 26300,
 'objLastChoose': 31896,
 'actLengthLongerChoose': 3258,
 'actLengthShorterChoose': 3258,
 'actLengthLongerVerify': 3258,
 'actLengthShorterVerify': 3258,
 'actTime': 38906,
 'actLongest': 315,
 'actWhatAfterAll': 306,
 'objTime': 64,
 'actLast': 142,
 'actWhatBefore': 137,
 'objLastVerify': 13416,
 'actShortest': 53,
 'objFirstVerify': 6250}

In [22]:
x1 = {'objWhatGeneral': 2651,
 'objWhat': 238003,
 'objWhatChoose': 26300,
 'objFirst': 24333,
 'objFirstChoose': 27554,
 'actFirst': 587,
 'objLast': 40245,
 'relTime': 39002,
 'objLastChoose': 31860,
 'actLengthLongerChoose': 3258,
 'actLengthShorterChoose': 3258,
 'actLengthLongerVerify': 3258,
 'actLengthShorterVerify': 3258,
 'actTime': 36862,
 'actLongest': 315,
 'actWhatAfterAll': 306,
 'objTime': 64,
 'actLast': 142,
 'actWhatBefore': 137,
 'actShortest': 53}

x2 = {'objWhatGeneral': 2651,
 'objWhat': 238003,
 'objFirst': 24333,
 'objFirstChoose': 27554,
 'actFirst': 587,
 'objLast': 40245,
 'relTime': 39386,
 'objWhatChoose': 26300,
 'objLastChoose': 31896,
 'actLengthLongerChoose': 3258,
 'actLengthShorterChoose': 3258,
 'actLengthLongerVerify': 3258,
 'actLengthShorterVerify': 3258,
 'actTime': 38906,
 'actLongest': 315,
 'actWhatAfterAll': 306,
 'objTime': 64,
 'actLast': 142,
 'actWhatBefore': 137,
 'objLastVerify': 13416,
 'actShortest': 53,
 'objFirstVerify': 6250}
for i in x2:
    if i not in x1:
        print(i)

objLastVerify
objFirstVerify


In [35]:
for i in by_t:
    if i not in by_t_bal:
        print(i)

objExists
objRelExists
relExists
actExists
objFirstVerify
objLastVerify
andObjRelExists
xorObjRelExists


#COMETOME
# Fixing structural balancing

So --- I am trying 2 things

- supposed to delete 706216 from objRelExists


1. Test 1 -- I do math.floor
- good because it keeps maybe a wider variety of questions
- bad because it will probably keep a larger segment of the questions being verify / logic....
- more important in training? but im not sure. 
- for objRelExists, it does 690878 deleteng


2. Test 2 I change back math.floor and then make it so that instead of only deleting 1 in info 3, it keeps it at deleting 2
- this is probably better because it actually will balance structural
- I just still have to make sure that it works
- When I tried doing ^^^^ changes, I got an issue where leftovers were not 0
- it is actually keeping questions (i think) though
- it also doesn't delete enough... 
- THough this might be because I did continue and not break? retrying. still getting leftover problems
- I think the leftover problems are because it's trying to delete more than we have
- for objRelExists, it does 701540 deleteng when continue I think?. also with continue


- ok now im getting thi which is wayyy lower than the amount i'm suspposded to delte

343020


OK I'm thinking the best might be to keep the only taking 1 and to floor, but then cut it off prematurely?

Like asy we need to keep x and then once you've reached the amount you can keep, keep it?
And maybe randomize the order of locals when iterating 


I'm going to get keeping from later on, though it may be the same? ALso i think i had a TODO of accounting for balancing extras so idk

ok still note deleting enoguh.. 342570


The problem was that instead of breaking, I should be deleting all of them
Which is mostly happening now because I changed it, except that I'm still a little bit off
so I had been keeping stuff

oh but might because del is differnet, so should be fine?

In [58]:

with open('../exports/dataset/test-del_by_video.txt', 'rb') as f:
     delbyv = json.load(f)


In [59]:
by_t_del = {} # COMETOME
for i, v_id in enumerate(delbyv):
    if i % 100 == 0:
        print(i)
    
    with open('../exports/dataset/smoothed/test/%s.txt' % v_id, 'rb') as f:
        QA = json.load(f)
        
    for q_id in delbyv[v_id]:
        q = QA[q_id]
        t = q['attributes']['type']
        
        if t not in by_t_del:
            by_t_del[t] = 0
        by_t_del[t] += 1

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800


In [60]:
by_t_del

{'andObjRelExists': 1064746,
 'xorObjRelExists': 920158,
 'objExists': 326302,
 'objRelExists': 706216,
 'relExists': 537922,
 'actExists': 1048076,
 'objFirstVerify': 191748,
 'objLastVerify': 96420,
 'relTime': 9282,
 'actTime': 39756,
 'objWhatChoose': 67706,
 'objLastChoose': 4516}

In [ ]:
for v_id in delbyv:
    stuff = {}
    for q_id in delbyv[v_id]:
        if q_id in stuff:
            print('Repeat: ', q_id)
            stuff[q_id] += 1
            
        stuff[q_id] = 1
        
        

In [43]:

with open('../exports/dataset/test-info4.txt', 'rb') as f:
     info = json.load(f)

#printInfo2(info)

In [44]:

def printInfo3(info):
    print("TOTAL: ", info['total'])
    for struct in info['struct']:
        print()
        s = info['struct'][struct]
        print(" "*4, struct, s['total'])
        if 'num_del' in info['struct'][struct]:
            print(" "*5, "delete", s['num_del'])
            print(" "*5, "leave", s['total'] - s['num_del'])
        for templ in info['struct'][struct]['templ']:
            t = info['struct'][struct]['templ'][templ]
            print(" "*8, templ, t['total'])
            if 'num_del' in t:
                print(" "*9, "delete", t['num_del'])
                print(" "*9, "leave", t['total'] - t['num_del'])
            tot_del = 0
            tot_leave = 0
            for local in t['local']:
                l = t['local'][local]
                if 'num_del' in l:
                    tot_del += l['num_del']
                    tot_leave += l['total'] - l['num_del']
                    
                if abs(l['total'] - l['num_del']) > 1:
                    print("%s delete %s out of %s" % (local, l['num_del'], l['total']))
                    
            print(" "*9, "delete from local", tot_del)
            print(" "*9, "leave from local", tot_leave)
            
# OK so the problem is that it's only deleting one from most of the things....
# so we'd need to keep 2 per local so that it's a yes and a no?
# maybe only for training?


# OK Test 1 -- I do math.floor
# Test 2 I change back math.floor and then make it so that instead of only deleting 1 in info 3, it keeps it at deleting 2

printInfo3(info)

TOTAL:  5639132

     logic 2015584
      delete 1984906
      leave 30678
         andObjRelExists 1080086
          delete 1064747
          leave 15339
          delete from local 1064747
          leave from local 15339
         xorObjRelExists 935498
          delete 920159
          leave 15339
          delete from local 920159
          leave from local 15339

     verify 3004526
      delete 2912494
      leave 92032
         objExists 341640
          delete 326302
          leave 15338
          delete from local 326302
          leave from local 15338
         objRelExists 721554
          delete 706216
          leave 15338
          delete from local 706216
          leave from local 15338
         relExists 553260
          delete 537922
          leave 15338
          delete from local 537922
          leave from local 15338
         actExists 1063414
          delete 1048076
          leave 15338
          delete from local 1048076
          leave from local 15338
    

yes-no-r7-o2-after-c061 delete 6 out of 8
yes-no-r7-o32-between-c151-c154 delete 2 out of 4
yes-no-r7-o17-between-c151-c154 delete 2 out of 4
yes-no-r7-o17-between-c151-c059 delete 2 out of 4
yes-no-r7-o32-between-c151-c061 delete 0 out of 2
yes-no-r8-o23-after-c014 delete 0 out of 2
yes-no-r8-o17-after-c027 delete 0 out of 2
yes-no-r8-o32-between-c117-c154 delete 0 out of 2
yes-no-r8-o2-between-c117-c061 delete 2 out of 4
yes-no-r8-o32-between-c027-c154 delete 0 out of 2
yes-no-r8-o17-between-c027-c154 delete 0 out of 2
yes-no-r8-o32-between-c027-c025 delete 0 out of 2
yes-no-r8-o17-between-c027-c025 delete 0 out of 2
yes-no-r8-o8-between-c027-c116 delete 0 out of 2
yes-no-r8-o32-between-c027-c062 delete 0 out of 2
yes-no-r6-o8-after-c032 delete 4 out of 6
yes-no-r6-o8-between-c014-c062 delete 0 out of 2
yes-no-r6-o8-between-c025-c116 delete 0 out of 2
yes-no-r6-o8-between-c032-c062 delete 0 out of 2
yes-no-r4-o23-after-c014 delete 0 out of 2
yes-no-r4-o17-after-c014 delete 2 out of 4

yes-no-r7-o32-after-c071 delete 4 out of 6
yes-no-r7-o32-while-c071 delete 2 out of 4
yes-no-r7-o23-between-c097-c151 delete 0 out of 2
yes-no-r9-o15-after-c012 delete 0 out of 2
yes-no-r6-o15-while-c110 delete 2 out of 4
yes-no-r6-o12-between-c097-c011 delete 0 out of 2
yes-no-r10-after-c012 delete 22 out of 24
yes-no-r15-o9-after-c022 delete 0 out of 2
yes-no-r6-o17-after-c114 delete 2 out of 4
yes-no-r6-o17-after-c112 delete 2 out of 4
yes-no-r8-o12-between-c112-c061 delete 0 out of 2
yes-no-r22-o6-after-c127 delete 0 out of 2
yes-no-r10-o6-after-c154 delete 0 out of 2
yes-no-r10-o6-between-c154-c009 delete 0 out of 2
yes-no-r6-o20-after-c059 delete 0 out of 2
yes-no-r6-o20-after-c040 delete 0 out of 2
yes-no-r6-o20-after-c044 delete 0 out of 2
yes-no-r6-o20-while-c040 delete 0 out of 2
yes-no-r6-o20-while-c044 delete 0 out of 2
yes-no-r6-o8-while-c042 delete 0 out of 2
yes-no-r6-o32-between-c009-c152 delete 0 out of 2
yes-no-r6-o32-between-c009-c149 delete 0 out of 2
yes-no-r6-o20-

yes-no-r10-o23-while-c021 delete 8 out of 10
yes-no-r10-o17-while-c115 delete 4 out of 6
yes-no-r10-o2-while-c115 delete 0 out of 2
yes-no-r10-o23-while-c020 delete 22 out of 24
yes-no-r10-o17-while-c118 delete 4 out of 6
yes-no-r10-o23-while-c118 delete 2 out of 4
yes-no-r10-o2-between-c030-c062 delete 0 out of 2
yes-no-r10-o2-between-c117-c062 delete 0 out of 2
yes-no-r6-o23-before-c107 delete 2 out of 4
yes-no-r6-o2-while-c107 delete 2 out of 4
yes-no-r6-o23-while-c128 delete 8 out of 10
yes-no-r6-o23-while-c110 delete 4 out of 6
yes-no-r6-o17-while-c021 delete 42 out of 44
yes-no-r6-o23-while-c020 delete 40 out of 42
yes-no-r6-o23-while-c119 delete 4 out of 6
yes-no-r8-o23-before-c107 delete 12 out of 14
yes-no-r8-o2-before-c107 delete 4 out of 6
yes-no-r8-o2-while-c107 delete 6 out of 8
yes-no-r8-o2-while-c026 delete 2 out of 4
yes-no-r8-o12-while-c020 delete 4 out of 6
yes-no-r4-o17-before-c023 delete 18 out of 20
yes-no-r4-o21-before-c062 delete 4 out of 6
yes-no-r4-o21-before-c

yes-no-r8-o6-before-c027 delete 0 out of 2
yes-no-r8-o8-before-c043 delete 12 out of 14
yes-no-r8-o6-before-c115 delete 0 out of 2
yes-no-r8-o12-before-c014 delete 2 out of 4
yes-no-r8-o8-before-c109 delete 4 out of 6
yes-no-r8-o23-before-c109 delete 0 out of 2
yes-no-r8-o8-before-c044 delete 16 out of 18
yes-no-r8-o8-before-c117 delete 0 out of 2
yes-no-r8-o8-while-c041 delete 34 out of 36
yes-no-r8-o23-while-c110 delete 8 out of 10
yes-no-r8-o6-while-c110 delete 2 out of 4
yes-no-r8-o6-while-c014 delete 0 out of 2
yes-no-r8-o23-while-c014 delete 8 out of 10
yes-no-r8-o6-while-c107 delete 2 out of 4
yes-no-r8-o6-while-c117 delete 0 out of 2
yes-no-r8-o12-between-c009-c115 delete 0 out of 2
yes-no-r8-o12-between-c009-c014 delete 0 out of 2
yes-no-r8-o32-between-c107-c110 delete 0 out of 2
yes-no-r8-o6-between-c107-c110 delete 4 out of 6
yes-no-r8-o32-between-c032-c110 delete 0 out of 2
yes-no-r22-o4-while-c151 delete 2 out of 4
yes-no-r16-o3-before-c011 delete 6 out of 8
yes-no-r16-o3-

...

r7-o4-o32-r7-o4-o32-after-c025 delete 0 out of 2
r7-o32-o4-r7-o32-o4-after-c025 delete 0 out of 4
r7-o23-o4-r7-o23-o4-after-c113 delete 0 out of 10
r7-o22-o4-r7-o22-o4-after-c113 delete 0 out of 22
r7-o4-o32-r7-o4-o32-after-c113 delete 0 out of 38
r7-o4-o23-r7-o4-o23-after-c113 delete 0 out of 10
r7-o4-o22-r7-o4-o22-after-c113 delete 0 out of 6
r7-o32-o22-r7-o32-o22-after-c113 delete 0 out of 10
r7-o32-o4-r7-o32-o4-after-c113 delete 0 out of 62
r7-o4-o32-r7-o4-o32-while-c028 delete 0 out of 2
r7-o32-o4-r7-o32-o4-while-c028 delete 0 out of 4
r7-o23-o32-r7-o23-o32-after-c113 delete 0 out of 8
r7-o22-o32-r7-o22-o32-after-c113 delete 0 out of 8
r7-o21-o17-r7-o21-o17-after-c110 delete 0 out of 2
r8-o12-o32-r8-o12-o32-after-c104 delete 0 out of 8
r8-o3-o32-r8-o3-o32-after-c072 delete 0 out of 14
r8-o12-o32-r8-o12-o32-after-c072 delete 0 out of 12
r8-o4-o20-r8-o4-o20-after-c134 delete 0 out of 14
r8-o12-o32-r8-o12-o32-after-c134 delete 0 out of 14
r8-o12-o32-r8-o12-o32-after-c133 delete 0 out

r7-o32-o23-r7-o32-o23-while-c061 delete 1 out of 22
r7-o23-o32-r7-o23-o32-while-c065 delete 0 out of 6
r6-o32-o17-r6-o32-o17-all- delete 1 out of 22
r6-o23-o17-r6-o23-o17-all- delete 0 out of 8
r6-o17-o32-r6-o17-o32-all- delete 0 out of 16
r6-o17-o23-r6-o17-o23-all- delete 0 out of 4
r6-o32-o17-r6-o32-o17-while-c028 delete 0 out of 2
r6-o32-o17-r6-o32-o17-while-c059 delete 0 out of 12
r6-o32-o17-r6-o32-o17-while-c011 delete 0 out of 2
r6-o17-o32-r6-o17-o32-while-c011 delete 0 out of 4
r6-o32-o17-r6-o32-o17-while-c009 delete 0 out of 12
r6-o23-o17-r6-o23-o17-while-c009 delete 0 out of 2
r6-o17-o32-r6-o17-o32-while-c009 delete 0 out of 8
r6-o17-o23-r6-o17-o23-while-c009 delete 0 out of 2
r8-o32-o8-r8-o32-o8-before-c065 delete 0 out of 14
r8-o32-o17-r8-o32-o17-all- delete 9 out of 30
r8-o32-o23-r8-o32-o23-all- delete 0 out of 16
r8-o8-o23-r8-o8-o23-all- delete 0 out of 10
r8-o23-o17-r8-o23-o17-all- delete 0 out of 14
r8-o17-o23-r8-o17-o23-all- delete 0 out of 16
r8-o32-o17-r8-o32-o17-whil

r22-o12-o17-r22-o12-o17-while-c038 delete 0 out of 8
r22-o17-o32-r22-o17-o32-while-c038 delete 29 out of 50
r22-o17-o12-r22-o17-o12-while-c038 delete 0 out of 20
r22-o19-o32-r22-o19-o32-while-c038 delete 0 out of 8
r22-o32-o4-r22-o32-o4-between-c120-c119 delete 0 out of 2
r22-o6-o32-r22-o6-o32-all- delete 0 out of 2
r22-o6-o32-r22-o6-o32-while-c011 delete 0 out of 2
r22-o6-o32-r22-o6-o32-while-c059 delete 0 out of 8
r8-o6-o32-r8-o6-o32-all- delete 0 out of 6
r8-o32-o6-r8-o32-o6-while-c059 delete 0 out of 8
r22-o14-o13-r22-o14-o13-before-c053 delete 19 out of 40
r22-o14-o15-r22-o14-o15-before-c053 delete 0 out of 10
r22-o14-o13-r22-o14-o13-before-c097 delete 0 out of 2
r6-o32-o10-r6-o32-o10-all- delete 0 out of 6
r7-o4-o3-r7-o4-o3-all- delete 3 out of 24
r8-o4-o36-r8-o4-o36-all- delete 0 out of 2
r8-o4-o12-r8-o4-o12-while-c092 delete 0 out of 2
r7-o4-o36-r7-o4-o36-all- delete 0 out of 4
r7-o36-o12-r7-o36-o12-all- delete 0 out of 2
r7-o36-o4-r7-o36-o4-all- delete 0 out of 4
r22-o12-o3-r2

r8-o12-o33-r8-o12-o33-while-c063 delete 0 out of 2
r8-o32-o12-r8-o32-o12-while-c063 delete 0 out of 6
r8-o32-o12-r8-o32-o12-while-c061 delete 1 out of 22
r8-o32-o12-r8-o32-o12-while-c065 delete 0 out of 12
r22-o12-o17-r22-o12-o17-while-c124 delete 0 out of 6
r22-o13-o14-r22-o13-o14-all- delete 0 out of 4
r7-o15-o32-r7-o15-o32-while-c152 delete 0 out of 4
r8-o15-o14-r8-o15-o14-before-c012 delete 0 out of 2
r8-o13-o23-r8-o13-o23-all- delete 0 out of 12
r6-o13-o14-r6-o13-o14-all- delete 0 out of 4
r22-o13-o12-r22-o13-o12-before-c152 delete 0 out of 2
r22-o13-o12-r22-o13-o12-before-c149 delete 0 out of 2
r7-o13-o12-r7-o13-o12-before-c152 delete 0 out of 2
r7-o13-o12-r7-o13-o12-before-c149 delete 0 out of 2
r8-o22-o14-r8-o22-o14-all- delete 0 out of 2
r22-o9-o8-r22-o9-o8-all- delete 0 out of 6
r22-o8-o9-r22-o8-o9-all- delete 0 out of 6
r8-o9-o2-r8-o9-o2-before-c151 delete 0 out of 2
r8-o2-o9-r8-o2-o9-before-c151 delete 0 out of 2
r8-o2-o17-r8-o2-o17-before-c151 delete 0 out of 2
r8-o21-o32-

          leave from local 53


In [51]:
1080086 + 935498

2015584

In [24]:

def printInfo2(info):
    print("TOTAL: ", info['total'])
    for struct in info['struct']:
        print()
        s = info['struct'][struct]
        print(" "*4, struct, s['total'])
        if 'num_del' in info['struct'][struct]:
            print(" "*5, "delete", s['num_del'])
            print(" "*5, "leave", s['total'] - s['num_del'])
        for templ in info['struct'][struct]['templ']:
            t = info['struct'][struct]['templ'][templ]
            print(" "*8, templ, t['total'])
            if 'num_del' in t:
                print(" "*9, "delete", t['num_del'])
                print(" "*9, "leave", t['total'] - t['num_del'])
            tot_del = 0
            tot_leave = 0
            for local in t['local']:
                l = t['local'][local]
                if 'num_del' in l:
                    tot_del += l['num_del']
                    tot_leave += l['total'] - l['num_del']
                    
            print(" "*9, "delete from local", tot_del)
            print(" "*9, "leave from local", tot_leave)
            

                        
printInfo2(info)

TOTAL:  5639132

     logic 2015584
      delete 1984906
      leave 30678
         andObjRelExists 1080086
          delete 1064747
          leave 15339
          delete from local 1064747
          leave from local 15339
         xorObjRelExists 935498
          delete 920159
          leave 15339
          delete from local 920159
          leave from local 15339

     verify 3004526
      delete 2912494
      leave 92032
         objExists 341640
          delete 326302
          leave 15338
          delete from local 326302
          leave from local 15338
         objRelExists 721554
          delete 706216
          leave 15338
          delete from local 706216
          leave from local 15338
         relExists 553260
          delete 537922
          leave 15338
          delete from local 537922
          leave from local 15338
         actExists 1063414
          delete 1048076
          leave 15338
          delete from local 1048076
          leave from local 15338
    

In [ ]:

def getQidsToDel(info):
    to_del = []
    for struct in info['struct']:
        print(struct)
        if info['struct'][struct]['num_del'] == 0:
            continue
        for templ in info['struct'][struct]['templ']:
            if info['struct'][struct]['templ'][templ]['num_del'] == 0:
                continue
            print("  ", templ)
            for loc in info['struct'][struct]['templ'][templ]['local']:
                l = info['struct'][struct]['templ'][templ]['local'][loc]
                num_del = l['num_del']
                deleted = 0
                
                if num_del == 0:
                    l['remaining'] = l['total']
                    continue
                
                if len(l['answer']) < 2:
                    for a in l['answer']:
                        for tt in l['answer'][a]:
                            to_del.append(l['answer'][a][tt])
                    l['remaining'] = 0
                    continue
                    
                if len(l['answer']) > 2:
                    delete = deleteXFromDistr(l['answer'], l['num_del'])
                    for i in l['answer']:
                        to_del.append(random.sample(l['answer'][i], k=delete[i]))
                    continue
                    
                
                dist = []
                for a in l['answer']:
                    dist.append((a, l['answer'][a]))
                (a1, lst1), (a2, lst2) = dist
                cnt1 = sums(lst1)
                cnt2 = sums(lst2)
                if cnt1 != cnt2:
                    if cnt1 < cnt2:
                        diff = cnt2 - cnt1
                        if diff >= num_del: 
                            num_del2 = num_del
                            num_del1 = 0
                            deleted = num_del
                        else:
                            num_del = math.ceil(abs(num_del - diff) / 2)
                            deleted = 2 * num_del + diff
                            num_del1 = num_del
                            num_del2 = num_del + diff
                    if cnt2 < cnt1:
                        diff = cnt1 - cnt2
                        if diff >= num_del: 
                            num_del1 = num_del
                            num_del2 = 0
                            deleted = num_del
                        else:
                            num_del = math.ceil(abs(num_del - diff) / 2)
                            deleted = 2 * num_del + diff
                            num_del2 = num_del
                            num_del1 = num_del + diff
                else:
                    num_del1 = math.ceil(num_del / 2)
                    num_del2 = math.ceil(num_del / 2)
                    deleted += 2 * num_del1
                to_add1 = bs.getIdsToDelete(l['answer'][a1], num_del1)
                
                for i in to_add1:
                    if type(i) == dict:
                        print("There is something in add1 that is a dict")
                        print(to_add1)
                if type(to_add1) == dict:
                    print("to add 1 is a dict")
                    
                if 'no_temporal' == to_add1:
                    print("no temporal is to_add 1")
                #print(to_add1)
                to_add2 = bs.getIdsToDelete(l['answer'][a2], num_del2)
                
                
                for i in to_add2:
                    if type(i) == dict:
                        print("There is something in add2 that is a dict")
                        print(to_add2)
                        
                if type(to_add2) == dict:
                    print("to add 2 is a dict")
                to_del.append(to_add1)
                to_del.append(to_add2)
                
                for lst in to_del:
                    if '0Z1PC-192974' in lst:
                        print("LIST that includes thing in dic")
                    #if type(lst) == dict:
                    #    print("add 1", to_add1)
                    #    print("add 2", to_add2)
                    #    print("list is", lst)
                    #    print("Checking", templ, loc)
                    #    print("List is a dict")
                #if 'no_temporal' in to_del:
                #    print('Same ans in to_del')
                if 'no_temporal' == to_add2:
                    print("no temporal is to_add2")

                l['remaining'] = l['total'] - deleted # TODO: add in any balancing extras had here too
    
        print("checking todel after ", struct)
        
        # so there is always in to_del
        for lst in to_del:
            if type(lst) == dict:
                print("List is a dict")
            #if 'no_temporal' in lst:
            #    print("no temporal is not in list in to del")
            #    print(type(lst))
            #    print(lst)
            #if lst == 'no_temporal':
            #    print("list is notemporal")

    

In [41]:

def printInfo(info, local):
    print("TOTAL: ", info['total'])
    for struct in info['struct']:
        print()
        s = info['struct'][struct]
        print(" "*4, struct, s['total'])
        if 'num_del' in info['struct'][struct]:
            print(" "*5, "delete", s['num_del'])
            print(" "*5, "leave", s['total'] - s['num_del'])
        for templ in info['struct'][struct]['templ']:
            t = info['struct'][struct]['templ'][templ]
            print(" "*8, templ, t['total'])
            if 'num_del' in t:
                print(" "*9, "delete", t['num_del'])
                print(" "*9, "leave", t['total'] - t['num_del'])
            if local: 
                for local in t['local']:
                    l = t['local'][local]
                    print(" "*16, local, l['total'])
                    if 'num_del' in l:
                        print(" "*17, "delete", l['num_del'])
                        print(" "*17, "leave", l['total'] - l['num_del'])


In [43]:

with open('../exports/dataset/test-info0.txt', 'rb') as f:
     info = json.load(f)

printInfo(info, False)

TOTAL:  5639132

     logic 2015584
         andObjRelExists 1080086
         xorObjRelExists 935498

     verify 3004526
         objExists 341640
         objRelExists 721554
         relExists 553260
         actExists 1063414
         objFirstVerify 210978
         objLastVerify 113680

     compare 141714
         relTime 48832
         actLengthLongerChoose 3258
         actLengthShorterChoose 3258
         actLengthLongerVerify 3258
         actLengthShorterVerify 3258
         actTime 79786
         objTime 64

     choose 170536
         objWhatChoose 105884
         objFirstChoose 27554
         objLastChoose 37098

     query 306772
         objWhatGeneral 2651
         objWhat 238003
         objFirst 24333
         actFirst 587
         objLast 40245
         actLongest 315
         actWhatAfterAll 306
         actLast 142
         actWhatBefore 137
         actShortest 53


In [44]:

with open('../exports/dataset/test-info1.txt', 'rb') as f:
     info = json.load(f)

printInfo(info, False)

TOTAL:  5639132

     logic 2015584
      delete 1984906
      leave 30678
         andObjRelExists 1080086
         xorObjRelExists 935498

     verify 3004526
      delete 2912494
      leave 92032
         objExists 341640
         objRelExists 721554
         relExists 553260
         actExists 1063414
         objFirstVerify 210978
         objLastVerify 113680

     compare 141714
      delete 49682
      leave 92032
         relTime 48832
         actLengthLongerChoose 3258
         actLengthShorterChoose 3258
         actLengthLongerVerify 3258
         actLengthShorterVerify 3258
         actTime 79786
         objTime 64

     choose 170536
      delete 78504
      leave 92032
         objWhatChoose 105884
         objFirstChoose 27554
         objLastChoose 37098

     query 306772
      delete 0
      leave 306772
         objWhatGeneral 2651
         objWhat 238003
         objFirst 24333
         actFirst 587
         objLast 40245
         actLongest 315
         actWhat

In [52]:

with open('../exports/dataset/test-info2.txt', 'rb') as f:
     info = json.load(f)

printInfo2(info)

TOTAL:  5639132

     logic 2015584
      delete 1984906
      leave 30678
         andObjRelExists 1080086
          delete 1064747
          leave 15339
          delete from local 0
          leave from local 0
         xorObjRelExists 935498
          delete 920159
          leave 15339
          delete from local 0
          leave from local 0

     verify 3004526
      delete 2912494
      leave 92032
         objExists 341640
          delete 326302
          leave 15338
          delete from local 0
          leave from local 0
         objRelExists 721554
          delete 706216
          leave 15338
          delete from local 0
          leave from local 0
         relExists 553260
          delete 537922
          leave 15338
          delete from local 0
          leave from local 0
         actExists 1063414
          delete 1048076
          leave 15338
          delete from local 0
          leave from local 0
         objFirstVerify 210978
          delete 195640
     

In [55]:

with open('../exports/dataset/test-info3.txt', 'rb') as f:
     info = json.load(f)

printInfo2(info)

TOTAL:  5639132

     logic 2015584
      delete 1984906
      leave 30678
         andObjRelExists 1080086
          delete 1064747
          leave 15339
          delete from local 1064747
          leave from local 15339
         xorObjRelExists 935498
          delete 920159
          leave 15339
          delete from local 920159
          leave from local 15339

     verify 3004526
      delete 2912494
      leave 92032
         objExists 341640
          delete 326302
          leave 15338
          delete from local 326302
          leave from local 15338
         objRelExists 721554
          delete 706216
          leave 15338
          delete from local 706216
          leave from local 15338
         relExists 553260
          delete 537922
          leave 15338
          delete from local 537922
          leave from local 15338
         actExists 1063414
          delete 1048076
          leave 15338
          delete from local 1048076
          leave from local 15338
    

In [ ]:

     logic 2015584
      delete 1984906
      leave 30678
         andObjRelExists 1080086
          delete 1064747
          leave 15339
         xorObjRelExists 935498
          delete 920159
          leave 15339

In [86]:
import numpy as np

In [84]:
feature = np.zeros((36, 2048), dtype='d')
print('type before', feature.dtype)
feature = feature.astype(np.longdouble)
print('type after', feature.dtype)
#torch.from_numpy(feature)


type before float64
type after float128
